In [30]:
#Section 0: Initialization and Data setup

In [31]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn import metrics 
import warnings
warnings.filterwarnings('ignore')
%matplotlib inline

#Loading the dataset
test_data = pd.read_csv('TargetData.csv')


#Print the first 5 rows of the dataframe.
test_data.head()

'''
failure = pd.read_csv('TargetData.csv')
target = ['multilabels', 'SB', 'ROW', 'COL']
y = [None] * len(target)

y[0] = failure[['SB', 'ROW', 'COL']].values
n_classes = y[0].shape[1]

for (i, j) in zip(range(1, len(target)), ['SB', 'ROW', 'COL']):
    y[i] = failure[j].values

    print(y[i])
raise
'''
#X consists of 58 features. Each feature represents 1 test in the long test flow.
X = test_data.drop([ 'gallop 1', 'gallop 5', 'Row Shift 7',"ID","SB","COL","Margin","Block","ROW"],axis = 1)
#Y can be one of ROW,COL,SB. ROW means the failure is on a row of memory array. 
#COL means the failure is on a column of the cell array.
#SB is single bit failure inside the memory.
#Pre-pruning involves removal of columns with no toggle in value such as in 'gallop 1', 'gallop 5', 'Row Shift 7'.
#Pre-pruning also remove columns with all unique value at all entries such as "ID"

#Forming multilabel [SB,COL,ROW]
#['Overkill','SB','COL','SB+COL','ROW','ROW+SB','ROW+COL','SB+ROW+COL']
y=test_data[["SB","COL","ROW"]].as_matrix()
#y = test_data.SB+2*test_data.COL+4*test_data.ROW #alternative as a class of 8 values from 0 to 7.

#y = test_data.ROW #COL #SB #if debugging, use single label


#importing train_test_split
#perfrom train and test data split
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test = train_test_split(X,y,test_size=1/3,random_state=2, stratify=y)

#scalar transformation is done on all models for easy comparison later.
scaler = StandardScaler()  
scaler.fit(X_train)
X_train = scaler.transform(X_train)    
X_test = scaler.transform(X_test)  
X_test1=X_test
X_test2=X_test

X_train_b,X_test_b,y_train_b,y_test_b=X_train,X_test,y_train,y_test

In [32]:
#Section 1: Building Random Forest based on Single Decision Tree


In [33]:
#Section 1.1 Single class decision tree 

In [34]:
#Section 1.1.1 Post pruning function on decision tree
from sklearn.tree._tree import TREE_LEAF

def is_leaf(inner_tree, index):
    # Check whether node is leaf node
    return (inner_tree.children_left[index] == TREE_LEAF and 
            inner_tree.children_right[index] == TREE_LEAF)

def prune_index(inner_tree, decisions, index=0):
    # Start pruning from the bottom - if we start from the top, we might miss
    # nodes that become leaves during pruning.
    # Do not use this directly - use prune_duplicate_leaves instead.
    if not is_leaf(inner_tree, inner_tree.children_left[index]):
        prune_index(inner_tree, decisions, inner_tree.children_left[index])
    if not is_leaf(inner_tree, inner_tree.children_right[index]):
        prune_index(inner_tree, decisions, inner_tree.children_right[index])

    # Prune children if both children are leaves now and make the same decision:     
    if (is_leaf(inner_tree, inner_tree.children_left[index]) and
        is_leaf(inner_tree, inner_tree.children_right[index]) and
        (decisions[index] == decisions[inner_tree.children_left[index]]) and 
        (decisions[index] == decisions[inner_tree.children_right[index]])):
        # turn node into a leaf by "unlinking" its children
        inner_tree.children_left[index] = TREE_LEAF
        inner_tree.children_right[index] = TREE_LEAF
        ##print("Pruned {}".format(index))

#to be called later for single decision tree pruning.
def prune_duplicate_leaves(mdl):
    # Remove leaves if both 
    decisions = mdl.tree_.value.argmax(axis=2).flatten().tolist() # Decision for each node
    prune_index(mdl.tree_, decisions)

In [35]:
#Section 1.1.2 Building Single Decision Tree
#This is aimed to build a single decision tree with suitable depth and then fine tuned with suitable parameters
#In this case, multi-label decision tree is built
#In this scenario, to avoid exhaustive grid search, best depth is first to be identified before fine tuning min_impurity_decrease and min_weight_fraction_leaf

from sklearn.tree import DecisionTreeClassifier

max_accuracy=0
best_depth=12
best_impurity_decrease=0.0001
best_weight_fraction_leaf=0.001
non_improve_count=0

#Section 1.1.2.1 Find best depth in range of 20-40. This is because The total feature is 58, so suitable range should be in 20-40.
for DEPTH in range(20,40,1):
    dt = DecisionTreeClassifier(criterion='entropy',max_depth=DEPTH,random_state=0,min_impurity_decrease=0.0001,min_weight_fraction_leaf=0.001)
    dt.fit(X_train, y_train)
    #post_pruning
    prune_duplicate_leaves(dt)

    print(DEPTH,dt.score(X_test, y_test))
    if dt.score(X_test, y_test)>max_accuracy: 
        max_accuracy=dt.score(X_test, y_test)
        best_depth=DEPTH
        #prints for tuning the DEPTH - Best DEPTH = 29
        print("DEPTH = ", DEPTH)
    else:
        non_improve_count+=1
        
    if non_improve_count==4: break

#Section 1.1.2.2 Select best impurity decrease. Range in between 0.00005 to 0.0002. Based on the best Depth found earlier.   
non_improve_count=0
for impurity_decrease in range(5,20,1):

    dt = DecisionTreeClassifier(criterion='entropy',max_depth=best_depth,random_state=0,min_impurity_decrease=impurity_decrease*0.00001,min_weight_fraction_leaf=0.001)
    dt.fit(X_train, y_train)

    #post_pruning
    prune_duplicate_leaves(dt)

    print(best_depth,impurity_decrease,dt.score(X_test, y_test))
    if dt.score(X_test, y_test)>max_accuracy: 
        max_accuracy=dt.score(X_test, y_test)
        best_impurity_decrease=impurity_decrease*0.00001
    else:
        non_improve_count+=1
        
    if non_improve_count==3: break

#Section 1.1.2.2 Select best weight fraction leaf. Range in between 0.00005 to 0.0002. Based on the best Depth found earlier.      
non_improve_count=0        
for weight_fraction_leaf in range(5,15,1):
    dt = DecisionTreeClassifier(criterion='entropy',max_depth=best_depth,random_state=0,min_impurity_decrease=best_impurity_decrease,min_weight_fraction_leaf=weight_fraction_leaf*0.0001)
    dt.fit(X_train, y_train)
    #post_pruning
    prune_duplicate_leaves(dt)

    print(best_depth,best_impurity_decrease,weight_fraction_leaf,dt.score(X_test, y_test))
    if dt.score(X_test, y_test)>max_accuracy: 
        max_accuracy=dt.score(X_test, y_test)
        best_weight_fraction_leaf=weight_fraction_leaf*0.0001
    else:
        non_improve_count+=1
        
    if non_improve_count==3: break
    
#Section 1.1.2.3 Evaluating the best decision tree so far
dt = DecisionTreeClassifier(criterion='entropy',max_depth=best_depth,random_state=0,min_impurity_decrease=best_impurity_decrease,min_weight_fraction_leaf=best_weight_fraction_leaf)
dt.fit(X_train, y_train)    

#post_pruning
prune_duplicate_leaves(dt)

print(dt)
print("selected depth: {:d}".format(best_depth))
print("selected best_impurity_decrease: {:.8f}".format(best_impurity_decrease))
print("selected best_weight_fraction_leaf: {:.8f}".format(best_weight_fraction_leaf))
print("Accuracy on training set: {:.3f}".format(dt.score(X_train, y_train)))
print("Accuracy on test set: {:.3f}".format(dt.score(X_test, y_test)))

20 0.5227934044616876
DEPTH =  20
21 0.527643064985451
DEPTH =  21
22 0.5286129970902037
DEPTH =  22
23 0.5402521823472357
DEPTH =  23
24 0.5480116391852571
DEPTH =  24
25 0.5499515033947624
DEPTH =  25
26 0.5499515033947624
27 0.5499515033947624
28 0.5615906886517944
DEPTH =  28
29 0.5635305528612997
DEPTH =  29
30 0.5635305528612997
31 0.5645004849660524
DEPTH =  31
32 0.5596508244422891
31 5 0.5664403491755577
31 6 0.5664403491755577
31 7 0.5664403491755577
31 8 0.5645004849660524
31 5e-05 5 0.5674102812803103
31 5e-05 6 0.5674102812803103
31 5e-05 7 0.5674102812803103
31 5e-05 8 0.5674102812803103
DecisionTreeClassifier(class_weight=None, criterion='entropy', max_depth=31,
                       max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=5e-05, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0005, presort=False,
                       random_state=0, 

In [36]:
#Section 1.1.2.4 Visualizing the best decision tree so far
#DT visualizatin method 3
#!conda install -y pydotplus
from sklearn.tree import export_graphviz
from sklearn.externals.six import StringIO  
from IPython.display import Image  
import pydotplus
import os
os.environ["PATH"] += os.pathsep + 'C:/Program Files (x86)/Graphviz2.38/bin/'
#os.environ["PATH"] += os.pathsep + 'C:/Users/boonping/graphviz-2.38/release/bin'

dot_data = StringIO()
export_graphviz(dt, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True,feature_names = X.columns,class_names=['Overkill','SB','COL','SB+COL','ROW','ROW+SB','ROW+COL','SB+ROW+COL'])
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
graph.write_png('testClassified.png')
Image(graph.create_png())

In [37]:
#1.1.2.5 Evaluating confusion matrix and accuracy using single decision tree
#multi-class decision tree
y_pred = dt.predict(X_test)
from sklearn.metrics import classification_report, confusion_matrix,  multilabel_confusion_matrix  

print(multilabel_confusion_matrix(y_test, y_pred))  
print(classification_report(y_test, y_pred)) 

[[[461  67]
  [105 398]]

 [[527  57]
  [122 325]]

 [[654  39]
  [145 193]]]
              precision    recall  f1-score   support

           0       0.86      0.79      0.82       503
           1       0.85      0.73      0.78       447
           2       0.83      0.57      0.68       338

   micro avg       0.85      0.71      0.77      1288
   macro avg       0.85      0.70      0.76      1288
weighted avg       0.85      0.71      0.77      1288
 samples avg       0.68      0.60      0.62      1288



In [38]:
#1.1.2.6 Printing Feature Importance of a single decision tree
print(dt.feature_importances_)
#print(sorted(dt.feature_importances_))

ranked_feature=[]
leng=len(dt.feature_importances_)
for i in range(leng):
    ranked_feature.append('')
sorted_importance=sorted(dt.feature_importances_)
for i in range( len(dt.feature_importances_) ):
    if dt.feature_importances_[i]>0.20*sorted_importance[-1] or sorted_importance.index(dt.feature_importances_[i]) > len(dt.feature_importances_)-best_depth-1:
        #print(i)
        ranked_feature[leng-1-sorted_importance.index(dt.feature_importances_[i])]=test_data.columns[i+1]
        
for f in ranked_feature:
    if f != "":
        print(f)
    

[0.01560943 0.03021132 0.03880545 0.02683707 0.04458343 0.01856899
 0.00120957 0.04082627 0.01524956 0.00744262 0.03223181 0.00994719
 0.03972359 0.13871034 0.00836632 0.01765827 0.04055668 0.04172812
 0.19188984 0.00157623 0.00260677 0.00207156 0.00231282 0.01103879
 0.01382818 0.02736821 0.01484259 0.00448706 0.         0.
 0.00101243 0.01195434 0.0075333  0.01393681 0.00566164 0.0262039
 0.00661693 0.00108942 0.00245393 0.0022561  0.00049821 0.03546513
 0.00112253 0.00322725 0.00300803 0.0037925  0.         0.00152062
 0.00413964 0.00544327 0.01182472 0.00061102 0.000568   0.0063172
 0.00345501]
gallop 2
Column Short Type 3
Row Shift 1
long activation 2
Slow row 1
Long pause 2
walking digit 2
gallop 1
Amplifier 5
Activate-to-read 1
long activation 1
Row Shift 2
Fast Row Precharge 1
Row Shift 4
Column Short Type 1
Slow row 2
cell charge
Column Short Type 2
Row Shift 3
Amplifier 2
gallop 3
very late write 2
Amplifier 8
walking digit 3
walking digit 1
Amplifier 1
gallop 5
Long pause 1


In [39]:
#1.1.3 Develop best single decision tree into random forest for further optimization
from sklearn.ensemble import RandomForestClassifier

#Allow more randomness at random forest. Allow tress to grow deeper.
max_depth=best_depth+15
if max_depth>50:
    max_depth=50
dt=eval("RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',\
            max_depth=%s, max_features='auto', max_leaf_nodes=None,\
            min_impurity_decrease=%s, min_impurity_split=None,\
            min_samples_leaf=1, min_samples_split=2,\
            min_weight_fraction_leaf=%s, n_estimators=256, n_jobs=None,\
            oob_score=False, random_state=0, verbose=0, warm_start=False)" % (max_depth,best_impurity_decrease,best_weight_fraction_leaf) )

dt.fit(X_train, y_train)   

for i in range(len(dt.estimators_)):
    print("tree %s" % i )
    #print(dt.estimators_[i])
    #post pruning each tree
    #prune_duplicate_leaves(dt.estimators_[i])
    #print(dt.estimators_[i])


print(dt)
print("selected depth: {:d}".format(best_depth))
print("selected best_impurity_decrease: {:.8f}".format(best_impurity_decrease))
print("selected best_weight_fraction_leaf: {:.8f}".format(best_weight_fraction_leaf))
print("Accuracy on training set (multilabel): {:.3f}".format(dt.score(X_train, y_train)))
print("Accuracy on test set(multilabel): {:.3f}".format(dt.score(X_test, y_test)))

print(dt.predict(X_test))
#raise

tree 0
tree 1
tree 2
tree 3
tree 4
tree 5
tree 6
tree 7
tree 8
tree 9
tree 10
tree 11
tree 12
tree 13
tree 14
tree 15
tree 16
tree 17
tree 18
tree 19
tree 20
tree 21
tree 22
tree 23
tree 24
tree 25
tree 26
tree 27
tree 28
tree 29
tree 30
tree 31
tree 32
tree 33
tree 34
tree 35
tree 36
tree 37
tree 38
tree 39
tree 40
tree 41
tree 42
tree 43
tree 44
tree 45
tree 46
tree 47
tree 48
tree 49
tree 50
tree 51
tree 52
tree 53
tree 54
tree 55
tree 56
tree 57
tree 58
tree 59
tree 60
tree 61
tree 62
tree 63
tree 64
tree 65
tree 66
tree 67
tree 68
tree 69
tree 70
tree 71
tree 72
tree 73
tree 74
tree 75
tree 76
tree 77
tree 78
tree 79
tree 80
tree 81
tree 82
tree 83
tree 84
tree 85
tree 86
tree 87
tree 88
tree 89
tree 90
tree 91
tree 92
tree 93
tree 94
tree 95
tree 96
tree 97
tree 98
tree 99
tree 100
tree 101
tree 102
tree 103
tree 104
tree 105
tree 106
tree 107
tree 108
tree 109
tree 110
tree 111
tree 112
tree 113
tree 114
tree 115
tree 116
tree 117
tree 118
tree 119
tree 120
tree 121
tree 122
tre

In [40]:
#Section 2: SVC

In [ ]:
from sklearn.svm import SVC
from sklearn.multiclass import OneVsRestClassifier
#scaler = StandardScaler()  
#scaler.fit(X_train) 
#X_train= scaler.transform(X_train)  
#X_test2= scaler.transform(X_test2) 
#svm=SVC(kernel="rbf", gamma=10, C=1) 
#loop set up to determine optimum value for C

#To avoid exhaustive grid search, Find best C_val in range of 1 to 10.
max_score = 0
optimal_C = 0
optimal_gamma = 0
gamma_value = 0.001

while gamma_value < 10:
    for C_val in range(1,10,1):
        svm=OneVsRestClassifier( SVC(kernel="rbf", gamma=gamma_value, C=C_val)  )
        svm.fit(X_train, y_train)
        predictions = svm.predict(X_test2)
        if svm.score(X_train, y_train) > max_score:
            max_score = svm.score(X_train, y_train)
            optimal_C = C_val
            optimal_gamma = gamma_value
        from sklearn.metrics import classification_report, confusion_matrix {
 "cells": [
  {
   "cell_type": "code",
   "execution_count": 30,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 0: Initialization and Data setup"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 31,
   "metadata": {
    "scrolled": false
   },
   "outputs": [],
   "source": [
    "import numpy as np\n",
    "import pandas as pd\n",
    "import matplotlib.pyplot as plt\n",
    "from sklearn.preprocessing import StandardScaler\n",
    "from sklearn import metrics \n",
    "import warnings\n",
    "warnings.filterwarnings('ignore')\n",
    "%matplotlib inline\n",
    "\n",
    "#Loading the dataset\n",
    "test_data = pd.read_csv('TargetData.csv')\n",
    "\n",
    "\n",
    "#Print the first 5 rows of the dataframe.\n",
    "test_data.head()\n",
    "\n",
    "'''\n",
    "failure = pd.read_csv('TargetData.csv')\n",
    "target = ['multilabels', 'SB', 'ROW', 'COL']\n",
    "y = [None] * len(target)\n",
    "\n",
    "y[0] = failure[['SB', 'ROW', 'COL']].values\n",
    "n_classes = y[0].shape[1]\n",
    "\n",
    "for (i, j) in zip(range(1, len(target)), ['SB', 'ROW', 'COL']):\n",
    "    y[i] = failure[j].values\n",
    "\n",
    "    print(y[i])\n",
    "raise\n",
    "'''\n",
    "#X consists of 58 features. Each feature represents 1 test in the long test flow.\n",
    "X = test_data.drop([ 'gallop 1', 'gallop 5', 'Row Shift 7',\"ID\",\"SB\",\"COL\",\"Margin\",\"Block\",\"ROW\"],axis = 1)\n",
    "#Y can be one of ROW,COL,SB. ROW means the failure is on a row of memory array. \n",
    "#COL means the failure is on a column of the cell array.\n",
    "#SB is single bit failure inside the memory.\n",
    "#Pre-pruning involves removal of columns with no toggle in value such as in 'gallop 1', 'gallop 5', 'Row Shift 7'.\n",
    "#Pre-pruning also remove columns with all unique value at all entries such as \"ID\"\n",
    "\n",
    "#Forming multilabel [SB,COL,ROW]\n",
    "#['Overkill','SB','COL','SB+COL','ROW','ROW+SB','ROW+COL','SB+ROW+COL']\n",
    "y=test_data[[\"SB\",\"COL\",\"ROW\"]].as_matrix()\n",
    "#y = test_data.SB+2*test_data.COL+4*test_data.ROW #alternative as a class of 8 values from 0 to 7.\n",
    "\n",
    "#y = test_data.ROW #COL #SB #if debugging, use single label\n",
    "\n",
    "\n",
    "#importing train_test_split\n",
    "#perfrom train and test data split\n",
    "from sklearn.model_selection import train_test_split\n",
    "X_train,X_test,y_train,y_test = train_test_split(X,y,test_size=1/3,random_state=2, stratify=y)\n",
    "\n",
    "#scalar transformation is done on all models for easy comparison later.\n",
    "scaler = StandardScaler()  \n",
    "scaler.fit(X_train)\n",
    "X_train = scaler.transform(X_train)    \n",
    "X_test = scaler.transform(X_test)  \n",
    "X_test1=X_test\n",
    "X_test2=X_test\n",
    "\n",
    "X_train_b,X_test_b,y_train_b,y_test_b=X_train,X_test,y_train,y_test"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 32,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 1: Building Random Forest based on Single Decision Tree\n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 33,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 1.1 Single class decision tree "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 34,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 1.1.1 Post pruning function on decision tree\n",
    "from sklearn.tree._tree import TREE_LEAF\n",
    "\n",
    "def is_leaf(inner_tree, index):\n",
    "    # Check whether node is leaf node\n",
    "    return (inner_tree.children_left[index] == TREE_LEAF and \n",
    "            inner_tree.children_right[index] == TREE_LEAF)\n",
    "\n",
    "def prune_index(inner_tree, decisions, index=0):\n",
    "    # Start pruning from the bottom - if we start from the top, we might miss\n",
    "    # nodes that become leaves during pruning.\n",
    "    # Do not use this directly - use prune_duplicate_leaves instead.\n",
    "    if not is_leaf(inner_tree, inner_tree.children_left[index]):\n",
    "        prune_index(inner_tree, decisions, inner_tree.children_left[index])\n",
    "    if not is_leaf(inner_tree, inner_tree.children_right[index]):\n",
    "        prune_index(inner_tree, decisions, inner_tree.children_right[index])\n",
    "\n",
    "    # Prune children if both children are leaves now and make the same decision:     \n",
    "    if (is_leaf(inner_tree, inner_tree.children_left[index]) and\n",
    "        is_leaf(inner_tree, inner_tree.children_right[index]) and\n",
    "        (decisions[index] == decisions[inner_tree.children_left[index]]) and \n",
    "        (decisions[index] == decisions[inner_tree.children_right[index]])):\n",
    "        # turn node into a leaf by \"unlinking\" its children\n",
    "        inner_tree.children_left[index] = TREE_LEAF\n",
    "        inner_tree.children_right[index] = TREE_LEAF\n",
    "        ##print(\"Pruned {}\".format(index))\n",
    "\n",
    "#to be called later for single decision tree pruning.\n",
    "def prune_duplicate_leaves(mdl):\n",
    "    # Remove leaves if both \n",
    "    decisions = mdl.tree_.value.argmax(axis=2).flatten().tolist() # Decision for each node\n",
    "    prune_index(mdl.tree_, decisions)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 35,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "20 0.5227934044616876\n",
      "DEPTH =  20\n",
      "21 0.527643064985451\n",
      "DEPTH =  21\n",
      "22 0.5286129970902037\n",
      "DEPTH =  22\n",
      "23 0.5402521823472357\n",
      "DEPTH =  23\n",
      "24 0.5480116391852571\n",
      "DEPTH =  24\n",
      "25 0.5499515033947624\n",
      "DEPTH =  25\n",
      "26 0.5499515033947624\n",
      "27 0.5499515033947624\n",
      "28 0.5615906886517944\n",
      "DEPTH =  28\n",
      "29 0.5635305528612997\n",
      "DEPTH =  29\n",
      "30 0.5635305528612997\n",
      "31 0.5645004849660524\n",
      "DEPTH =  31\n",
      "32 0.5596508244422891\n",
      "31 5 0.5664403491755577\n",
      "31 6 0.5664403491755577\n",
      "31 7 0.5664403491755577\n",
      "31 8 0.5645004849660524\n",
      "31 5e-05 5 0.5674102812803103\n",
      "31 5e-05 6 0.5674102812803103\n",
      "31 5e-05 7 0.5674102812803103\n",
      "31 5e-05 8 0.5674102812803103\n",
      "DecisionTreeClassifier(class_weight=None, criterion='entropy', max_depth=31,\n",
      "                       max_features=None, max_leaf_nodes=None,\n",
      "                       min_impurity_decrease=5e-05, min_impurity_split=None,\n",
      "                       min_samples_leaf=1, min_samples_split=2,\n",
      "                       min_weight_fraction_leaf=0.0005, presort=False,\n",
      "                       random_state=0, splitter='best')\n",
      "selected depth: 31\n",
      "selected best_impurity_decrease: 0.00005000\n",
      "selected best_weight_fraction_leaf: 0.00050000\n",
      "Accuracy on training set: 0.619\n",
      "Accuracy on test set: 0.567\n"
     ]
    }
   ],
   "source": [
    "#Section 1.1.2 Building Single Decision Tree\n",
    "#This is aimed to build a single decision tree with suitable depth and then fine tuned with suitable parameters\n",
    "#In this case, multi-label decision tree is built\n",
    "#In this scenario, to avoid exhaustive grid search, best depth is first to be identified before fine tuning min_impurity_decrease and min_weight_fraction_leaf\n",
    "\n",
    "from sklearn.tree import DecisionTreeClassifier\n",
    "\n",
    "max_accuracy=0\n",
    "best_depth=12\n",
    "best_impurity_decrease=0.0001\n",
    "best_weight_fraction_leaf=0.001\n",
    "non_improve_count=0\n",
    "\n",
    "#Section 1.1.2.1 Find best depth in range of 20-40. This is because The total feature is 58, so suitable range should be in 20-40.\n",
    "for DEPTH in range(20,40,1):\n",
    "    dt = DecisionTreeClassifier(criterion='entropy',max_depth=DEPTH,random_state=0,min_impurity_decrease=0.0001,min_weight_fraction_leaf=0.001)\n",
    "    dt.fit(X_train, y_train)\n",
    "    #post_pruning\n",
    "    prune_duplicate_leaves(dt)\n",
    "\n",
    "    print(DEPTH,dt.score(X_test, y_test))\n",
    "    if dt.score(X_test, y_test)>max_accuracy: \n",
    "        max_accuracy=dt.score(X_test, y_test)\n",
    "        best_depth=DEPTH\n",
    "        #prints for tuning the DEPTH - Best DEPTH = 29\n",
    "        print(\"DEPTH = \", DEPTH)\n",
    "    else:\n",
    "        non_improve_count+=1\n",
    "        \n",
    "    if non_improve_count==4: break\n",
    "\n",
    "#Section 1.1.2.2 Select best impurity decrease. Range in between 0.00005 to 0.0002. Based on the best Depth found earlier.   \n",
    "non_improve_count=0\n",
    "for impurity_decrease in range(5,20,1):\n",
    "\n",
    "    dt = DecisionTreeClassifier(criterion='entropy',max_depth=best_depth,random_state=0,min_impurity_decrease=impurity_decrease*0.00001,min_weight_fraction_leaf=0.001)\n",
    "    dt.fit(X_train, y_train)\n",
    "\n",
    "    #post_pruning\n",
    "    prune_duplicate_leaves(dt)\n",
    "\n",
    "    print(best_depth,impurity_decrease,dt.score(X_test, y_test))\n",
    "    if dt.score(X_test, y_test)>max_accuracy: \n",
    "        max_accuracy=dt.score(X_test, y_test)\n",
    "        best_impurity_decrease=impurity_decrease*0.00001\n",
    "    else:\n",
    "        non_improve_count+=1\n",
    "        \n",
    "    if non_improve_count==3: break\n",
    "\n",
    "#Section 1.1.2.2 Select best weight fraction leaf. Range in between 0.00005 to 0.0002. Based on the best Depth found earlier.      \n",
    "non_improve_count=0        \n",
    "for weight_fraction_leaf in range(5,15,1):\n",
    "    dt = DecisionTreeClassifier(criterion='entropy',max_depth=best_depth,random_state=0,min_impurity_decrease=best_impurity_decrease,min_weight_fraction_leaf=weight_fraction_leaf*0.0001)\n",
    "    dt.fit(X_train, y_train)\n",
    "    #post_pruning\n",
    "    prune_duplicate_leaves(dt)\n",
    "\n",
    "    print(best_depth,best_impurity_decrease,weight_fraction_leaf,dt.score(X_test, y_test))\n",
    "    if dt.score(X_test, y_test)>max_accuracy: \n",
    "        max_accuracy=dt.score(X_test, y_test)\n",
    "        best_weight_fraction_leaf=weight_fraction_leaf*0.0001\n",
    "    else:\n",
    "        non_improve_count+=1\n",
    "        \n",
    "    if non_improve_count==3: break\n",
    "    \n",
    "#Section 1.1.2.3 Evaluating the best decision tree so far\n",
    "dt = DecisionTreeClassifier(criterion='entropy',max_depth=best_depth,random_state=0,min_impurity_decrease=best_impurity_decrease,min_weight_fraction_leaf=best_weight_fraction_leaf)\n",
    "dt.fit(X_train, y_train)    \n",
    "\n",
    "#post_pruning\n",
    "prune_duplicate_leaves(dt)\n",
    "\n",
    "print(dt)\n",
    "print(\"selected depth: {:d}\".format(best_depth))\n",
    "print(\"selected best_impurity_decrease: {:.8f}\".format(best_impurity_decrease))\n",
    "print(\"selected best_weight_fraction_leaf: {:.8f}\".format(best_weight_fraction_leaf))\n",
    "print(\"Accuracy on training set: {:.3f}\".format(dt.score(X_train, y_train)))\n",
    "print(\"Accuracy on test set: {:.3f}\".format(dt.score(X_test, y_test)))"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 36,
   "metadata": {
    "scrolled": true
   },
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<IPython.core.display.Image object>"
      ]
     },
     "execution_count": 36,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "#Section 1.1.2.4 Visualizing the best decision tree so far\n",
    "#DT visualizatin method 3\n",
    "#!conda install -y pydotplus\n",
    "from sklearn.tree import export_graphviz\n",
    "from sklearn.externals.six import StringIO  \n",
    "from IPython.display import Image  \n",
    "import pydotplus\n",
    "import os\n",
    "os.environ[\"PATH\"] += os.pathsep + 'C:/Program Files (x86)/Graphviz2.38/bin/'\n",
    "#os.environ[\"PATH\"] += os.pathsep + 'C:/Users/boonping/graphviz-2.38/release/bin'\n",
    "\n",
    "dot_data = StringIO()\n",
    "export_graphviz(dt, out_file=dot_data,  \n",
    "                filled=True, rounded=True,\n",
    "                special_characters=True,feature_names = X.columns,class_names=['Overkill','SB','COL','SB+COL','ROW','ROW+SB','ROW+COL','SB+ROW+COL'])\n",
    "graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  \n",
    "graph.write_png('testClassified.png')\n",
    "Image(graph.create_png())"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 37,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "[[[461  67]\n",
      "  [105 398]]\n",
      "\n",
      " [[527  57]\n",
      "  [122 325]]\n",
      "\n",
      " [[654  39]\n",
      "  [145 193]]]\n",
      "              precision    recall  f1-score   support\n",
      "\n",
      "           0       0.86      0.79      0.82       503\n",
      "           1       0.85      0.73      0.78       447\n",
      "           2       0.83      0.57      0.68       338\n",
      "\n",
      "   micro avg       0.85      0.71      0.77      1288\n",
      "   macro avg       0.85      0.70      0.76      1288\n",
      "weighted avg       0.85      0.71      0.77      1288\n",
      " samples avg       0.68      0.60      0.62      1288\n",
      "\n"
     ]
    }
   ],
   "source": [
    "#1.1.2.5 Evaluating confusion matrix and accuracy using single decision tree\n",
    "#multi-class decision tree\n",
    "y_pred = dt.predict(X_test)\n",
    "from sklearn.metrics import classification_report, confusion_matrix,  multilabel_confusion_matrix  \n",
    "\n",
    "print(multilabel_confusion_matrix(y_test, y_pred))  \n",
    "print(classification_report(y_test, y_pred)) "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 38,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "[0.01560943 0.03021132 0.03880545 0.02683707 0.04458343 0.01856899\n",
      " 0.00120957 0.04082627 0.01524956 0.00744262 0.03223181 0.00994719\n",
      " 0.03972359 0.13871034 0.00836632 0.01765827 0.04055668 0.04172812\n",
      " 0.19188984 0.00157623 0.00260677 0.00207156 0.00231282 0.01103879\n",
      " 0.01382818 0.02736821 0.01484259 0.00448706 0.         0.\n",
      " 0.00101243 0.01195434 0.0075333  0.01393681 0.00566164 0.0262039\n",
      " 0.00661693 0.00108942 0.00245393 0.0022561  0.00049821 0.03546513\n",
      " 0.00112253 0.00322725 0.00300803 0.0037925  0.         0.00152062\n",
      " 0.00413964 0.00544327 0.01182472 0.00061102 0.000568   0.0063172\n",
      " 0.00345501]\n",
      "gallop 2\n",
      "Column Short Type 3\n",
      "Row Shift 1\n",
      "long activation 2\n",
      "Slow row 1\n",
      "Long pause 2\n",
      "walking digit 2\n",
      "gallop 1\n",
      "Amplifier 5\n",
      "Activate-to-read 1\n",
      "long activation 1\n",
      "Row Shift 2\n",
      "Fast Row Precharge 1\n",
      "Row Shift 4\n",
      "Column Short Type 1\n",
      "Slow row 2\n",
      "cell charge\n",
      "Column Short Type 2\n",
      "Row Shift 3\n",
      "Amplifier 2\n",
      "gallop 3\n",
      "very late write 2\n",
      "Amplifier 8\n",
      "walking digit 3\n",
      "walking digit 1\n",
      "Amplifier 1\n",
      "gallop 5\n",
      "Long pause 1\n",
      "random 2\n",
      "Row Shift 6\n",
      "gallop 6\n"
     ]
    }
   ],
   "source": [
    "#1.1.2.6 Printing Feature Importance of a single decision tree\n",
    "print(dt.feature_importances_)\n",
    "#print(sorted(dt.feature_importances_))\n",
    "\n",
    "ranked_feature=[]\n",
    "leng=len(dt.feature_importances_)\n",
    "for i in range(leng):\n",
    "    ranked_feature.append('')\n",
    "sorted_importance=sorted(dt.feature_importances_)\n",
    "for i in range( len(dt.feature_importances_) ):\n",
    "    if dt.feature_importances_[i]>0.20*sorted_importance[-1] or sorted_importance.index(dt.feature_importances_[i]) > len(dt.feature_importances_)-best_depth-1:\n",
    "        #print(i)\n",
    "        ranked_feature[leng-1-sorted_importance.index(dt.feature_importances_[i])]=test_data.columns[i+1]\n",
    "        \n",
    "for f in ranked_feature:\n",
    "    if f != \"\":\n",
    "        print(f)\n",
    "    "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 39,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "tree 0\n",
      "tree 1\n",
      "tree 2\n",
      "tree 3\n",
      "tree 4\n",
      "tree 5\n",
      "tree 6\n",
      "tree 7\n",
      "tree 8\n",
      "tree 9\n",
      "tree 10\n",
      "tree 11\n",
      "tree 12\n",
      "tree 13\n",
      "tree 14\n",
      "tree 15\n",
      "tree 16\n",
      "tree 17\n",
      "tree 18\n",
      "tree 19\n",
      "tree 20\n",
      "tree 21\n",
      "tree 22\n",
      "tree 23\n",
      "tree 24\n",
      "tree 25\n",
      "tree 26\n",
      "tree 27\n",
      "tree 28\n",
      "tree 29\n",
      "tree 30\n",
      "tree 31\n",
      "tree 32\n",
      "tree 33\n",
      "tree 34\n",
      "tree 35\n",
      "tree 36\n",
      "tree 37\n",
      "tree 38\n",
      "tree 39\n",
      "tree 40\n",
      "tree 41\n",
      "tree 42\n",
      "tree 43\n",
      "tree 44\n",
      "tree 45\n",
      "tree 46\n",
      "tree 47\n",
      "tree 48\n",
      "tree 49\n",
      "tree 50\n",
      "tree 51\n",
      "tree 52\n",
      "tree 53\n",
      "tree 54\n",
      "tree 55\n",
      "tree 56\n",
      "tree 57\n",
      "tree 58\n",
      "tree 59\n",
      "tree 60\n",
      "tree 61\n",
      "tree 62\n",
      "tree 63\n",
      "tree 64\n",
      "tree 65\n",
      "tree 66\n",
      "tree 67\n",
      "tree 68\n",
      "tree 69\n",
      "tree 70\n",
      "tree 71\n",
      "tree 72\n",
      "tree 73\n",
      "tree 74\n",
      "tree 75\n",
      "tree 76\n",
      "tree 77\n",
      "tree 78\n",
      "tree 79\n",
      "tree 80\n",
      "tree 81\n",
      "tree 82\n",
      "tree 83\n",
      "tree 84\n",
      "tree 85\n",
      "tree 86\n",
      "tree 87\n",
      "tree 88\n",
      "tree 89\n",
      "tree 90\n",
      "tree 91\n",
      "tree 92\n",
      "tree 93\n",
      "tree 94\n",
      "tree 95\n",
      "tree 96\n",
      "tree 97\n",
      "tree 98\n",
      "tree 99\n",
      "tree 100\n",
      "tree 101\n",
      "tree 102\n",
      "tree 103\n",
      "tree 104\n",
      "tree 105\n",
      "tree 106\n",
      "tree 107\n",
      "tree 108\n",
      "tree 109\n",
      "tree 110\n",
      "tree 111\n",
      "tree 112\n",
      "tree 113\n",
      "tree 114\n",
      "tree 115\n",
      "tree 116\n",
      "tree 117\n",
      "tree 118\n",
      "tree 119\n",
      "tree 120\n",
      "tree 121\n",
      "tree 122\n",
      "tree 123\n",
      "tree 124\n",
      "tree 125\n",
      "tree 126\n",
      "tree 127\n",
      "tree 128\n",
      "tree 129\n",
      "tree 130\n",
      "tree 131\n",
      "tree 132\n",
      "tree 133\n",
      "tree 134\n",
      "tree 135\n",
      "tree 136\n",
      "tree 137\n",
      "tree 138\n",
      "tree 139\n",
      "tree 140\n",
      "tree 141\n",
      "tree 142\n",
      "tree 143\n",
      "tree 144\n",
      "tree 145\n",
      "tree 146\n",
      "tree 147\n",
      "tree 148\n",
      "tree 149\n",
      "tree 150\n",
      "tree 151\n",
      "tree 152\n",
      "tree 153\n",
      "tree 154\n",
      "tree 155\n",
      "tree 156\n",
      "tree 157\n",
      "tree 158\n",
      "tree 159\n",
      "tree 160\n",
      "tree 161\n",
      "tree 162\n",
      "tree 163\n",
      "tree 164\n",
      "tree 165\n",
      "tree 166\n",
      "tree 167\n",
      "tree 168\n",
      "tree 169\n",
      "tree 170\n",
      "tree 171\n",
      "tree 172\n",
      "tree 173\n",
      "tree 174\n",
      "tree 175\n",
      "tree 176\n",
      "tree 177\n",
      "tree 178\n",
      "tree 179\n",
      "tree 180\n",
      "tree 181\n",
      "tree 182\n",
      "tree 183\n",
      "tree 184\n",
      "tree 185\n",
      "tree 186\n",
      "tree 187\n",
      "tree 188\n",
      "tree 189\n",
      "tree 190\n",
      "tree 191\n",
      "tree 192\n",
      "tree 193\n",
      "tree 194\n",
      "tree 195\n",
      "tree 196\n",
      "tree 197\n",
      "tree 198\n",
      "tree 199\n",
      "tree 200\n",
      "tree 201\n",
      "tree 202\n",
      "tree 203\n",
      "tree 204\n",
      "tree 205\n",
      "tree 206\n",
      "tree 207\n",
      "tree 208\n",
      "tree 209\n",
      "tree 210\n",
      "tree 211\n",
      "tree 212\n",
      "tree 213\n",
      "tree 214\n",
      "tree 215\n",
      "tree 216\n",
      "tree 217\n",
      "tree 218\n",
      "tree 219\n",
      "tree 220\n",
      "tree 221\n",
      "tree 222\n",
      "tree 223\n",
      "tree 224\n",
      "tree 225\n",
      "tree 226\n",
      "tree 227\n",
      "tree 228\n",
      "tree 229\n",
      "tree 230\n",
      "tree 231\n",
      "tree 232\n",
      "tree 233\n",
      "tree 234\n",
      "tree 235\n",
      "tree 236\n",
      "tree 237\n",
      "tree 238\n",
      "tree 239\n",
      "tree 240\n",
      "tree 241\n",
      "tree 242\n",
      "tree 243\n",
      "tree 244\n",
      "tree 245\n",
      "tree 246\n",
      "tree 247\n",
      "tree 248\n",
      "tree 249\n",
      "tree 250\n",
      "tree 251\n",
      "tree 252\n",
      "tree 253\n",
      "tree 254\n",
      "tree 255\n",
      "RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',\n",
      "                       max_depth=46, max_features='auto', max_leaf_nodes=None,\n",
      "                       min_impurity_decrease=5e-05, min_impurity_split=None,\n",
      "                       min_samples_leaf=1, min_samples_split=2,\n",
      "                       min_weight_fraction_leaf=0.0005, n_estimators=256,\n",
      "                       n_jobs=None, oob_score=False, random_state=0, verbose=0,\n",
      "                       warm_start=False)\n",
      "selected depth: 31\n",
      "selected best_impurity_decrease: 0.00005000\n",
      "selected best_weight_fraction_leaf: 0.00050000\n",
      "Accuracy on training set (multilabel): 0.629\n",
      "Accuracy on test set(multilabel): 0.592\n",
      "[[1 0 0]\n",
      " [0 1 1]\n",
      " [0 1 1]\n",
      " ...\n",
      " [1 0 0]\n",
      " [0 1 1]\n",
      " [1 1 1]]\n"
     ]
    }
   ],
   "source": [
    "#1.1.3 Develop best single decision tree into random forest for further optimization\n",
    "from sklearn.ensemble import RandomForestClassifier\n",
    "\n",
    "#Allow more randomness at random forest. Allow tress to grow deeper.\n",
    "max_depth=best_depth+15\n",
    "if max_depth>50:\n",
    "    max_depth=50\n",
    "dt=eval(\"RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',\\\n",
    "            max_depth=%s, max_features='auto', max_leaf_nodes=None,\\\n",
    "            min_impurity_decrease=%s, min_impurity_split=None,\\\n",
    "            min_samples_leaf=1, min_samples_split=2,\\\n",
    "            min_weight_fraction_leaf=%s, n_estimators=256, n_jobs=None,\\\n",
    "            oob_score=False, random_state=0, verbose=0, warm_start=False)\" % (max_depth,best_impurity_decrease,best_weight_fraction_leaf) )\n",
    "\n",
    "dt.fit(X_train, y_train)   \n",
    "\n",
    "for i in range(len(dt.estimators_)):\n",
    "    print(\"tree %s\" % i )\n",
    "    #print(dt.estimators_[i])\n",
    "    #post pruning each tree\n",
    "    #prune_duplicate_leaves(dt.estimators_[i])\n",
    "    #print(dt.estimators_[i])\n",
    "\n",
    "\n",
    "print(dt)\n",
    "print(\"selected depth: {:d}\".format(best_depth))\n",
    "print(\"selected best_impurity_decrease: {:.8f}\".format(best_impurity_decrease))\n",
    "print(\"selected best_weight_fraction_leaf: {:.8f}\".format(best_weight_fraction_leaf))\n",
    "print(\"Accuracy on training set (multilabel): {:.3f}\".format(dt.score(X_train, y_train)))\n",
    "print(\"Accuracy on test set(multilabel): {:.3f}\".format(dt.score(X_test, y_test)))\n",
    "\n",
    "print(dt.predict(X_test))\n",
    "#raise"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 40,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 2: SVC"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "from sklearn.svm import SVC\n",
    "from sklearn.multiclass import OneVsRestClassifier\n",
    "#scaler = StandardScaler()  \n",
    "#scaler.fit(X_train) \n",
    "#X_train= scaler.transform(X_train)  \n",
    "#X_test2= scaler.transform(X_test2) \n",
    "#svm=SVC(kernel=\"rbf\", gamma=10, C=1) \n",
    "#loop set up to determine optimum value for C\n",
    "\n",
    "#To avoid exhaustive grid search, Find best C_val in range of 1 to 10.\n",
    "max_score = 0\n",
    "optimal_C = 0\n",
    "optimal_gamma = 0\n",
    "gamma_value = 0.001\n",
    "\n",
    "while gamma_value < 10:\n",
    "    for C_val in range(1,10,1):\n",
    "        svm=OneVsRestClassifier( SVC(kernel=\"rbf\", gamma=gamma_value, C=C_val)  )\n",
    "        svm.fit(X_train, y_train)\n",
    "        predictions = svm.predict(X_test2)\n",
    "        if svm.score(X_train, y_train) > max_score:\n",
    "            max_score = svm.score(X_train, y_train)\n",
    "            optimal_C = C_val\n",
    "            optimal_gamma = gamma_value\n",
    "        from sklearn.metrics import classification_report, confusion_matrix \n",
    "        print(\"C= \", C_val)\n",
    "        print(\"gamma= \", gamma_value)\n",
    "        print(multilabel_confusion_matrix(y_test,predictions))  \n",
    "        print(classification_report(y_test,predictions)) \n",
    "        print(\"Accuracy on training set: {:.3f}\".format(svm.score(X_train, y_train)))\n",
    "        print(\"Accuracy on test set: {:.3f}\".format(svm.score(X_test2, y_test)))\n",
    "        print(\"============================================\")\n",
    "    gamma_value = gamma_value + 0.05\n",
    "    \n",
    "print(predictions)\n",
    "print(\">>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>\")\n",
    "print(\"optimal C = \", optimal_C)\n",
    "print(\"optimal gamma = \", optimal_gamma)\n",
    "\n",
    "\n",
    "#compute the best SVC with optimal C value.\n",
    "#svm_single=SVC(kernel=\"linear\", gamma='auto_deprecated', C=optimal_C, probability=True) \n",
    "#svm=OneVsRestClassifier( SVC(kernel=\"linear\", gamma='auto_deprecated', C=optimal_C, probability=True)  )\n",
    "svm=OneVsRestClassifier( SVC(kernel=\"rbf\", gamma=optimal_gamma, C=optimal_C)  )\n",
    "svm.fit(X_train, y_train)\n",
    "predictions = svm.predict(X_test2)\n",
    "svm_pred=predictions\n",
    "\n",
    "\n",
    "                                     \n",
    "                                     "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 42,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "'\\nmlp=MLPClassifier(activation=\\'logistic\\', alpha=0.9920073082747223,\\n              batch_size=\\'auto\\', beta_1=0.9, beta_2=0.999, early_stopping=True,\\n              epsilon=1e-08)\\nmlp.fit(X_train, y_train)\\nprint(mlp)\\n\\n#print(dt.predict(X_test))\\n\\nprint(svm)\\n\\n#print(svm.predict(X_test))\\n#Extracting ROW/COL/SB y and predict result from multilabel array as sklearn metrics may not support multilabel for bagging classifier.\\ny_train_row=[]\\ny_test_row=[]\\ndt_pred_row=[]\\nsvm_pred_row=[]\\nmlp_pred_row=[]\\nfor elem in y_train:\\n    y_train_row.append(elem[0])\\nfor elem in y_test:    \\n    y_test_row.append(elem[0])\\nfor elem in dt.predict(X_test):    \\n    dt_pred_row.append(elem[0])\\nfor elem in svm.predict(X_test):    \\n    svm_pred_row.append(elem[0])\\nfor elem in mlp.predict(X_test):    \\n    mlp_pred_row.append(elem[0])\\n    \\ny_train_col=[]\\ny_test_col=[]\\ndt_pred_col=[]\\nsvm_pred_col=[]\\nmlp_pred_col=[]\\nfor elem in y_train:\\n    y_train_col.append(elem[1])\\nfor elem in y_test:    \\n    y_test_col.append(elem[1])\\nfor elem in dt.predict(X_test):    \\n    dt_pred_col.append(elem[1])\\nfor elem in svm.predict(X_test):    \\n    svm_pred_col.append(elem[1])\\nfor elem in mlp.predict(X_test):    \\n    mlp_pred_col.append(elem[1])\\n    \\ny_train_sb=[]\\ny_test_sb=[]\\ndt_pred_sb=[]\\nsvm_pred_sb=[]\\nmlp_pred_sb=[]\\nfor elem in y_train:\\n    y_train_sb.append(elem[2])\\nfor elem in y_test:    \\n    y_test_sb.append(elem[2])\\nfor elem in dt.predict(X_test):    \\n    dt_pred_sb.append(elem[2])\\nfor elem in svm.predict(X_test):    \\n    svm_pred_sb.append(elem[2])\\nfor elem in mlp.predict(X_test):    \\n    mlp_pred_sb.append(elem[2])\\n        \\n#print(y_train_row)\\nfalse_pass_count=[\\n    confusion_matrix(y_test_row,dt_pred_row )[1][0] + confusion_matrix(y_test_col,dt_pred_col )[1][0] + confusion_matrix(y_test_sb,dt_pred_sb )[1][0],\\n    confusion_matrix(y_test_row,svm_pred_row )[1][0] + confusion_matrix(y_test_col,svm_pred_col )[1][0] + confusion_matrix(y_test_sb,svm_pred_sb )[1][0],\\n    confusion_matrix(y_test_row,mlp_pred_row ) [1][0] + confusion_matrix(y_test_col,mlp_pred_col )[1][0] + confusion_matrix(y_test_sb,mlp_pred_sb )[1][0]\\n]\\n\\n#print(false_pass_count[0])\\n    \\n\\ndt_row=dt.fit(X_train,y_train_row)\\ndt_col=dt.fit(X_train,y_train_col)\\ndt_sb=dt.fit(X_train,y_train_sb)\\n\\n\\nmlp_row=mlp.fit(X_train,y_train_row)\\nmlp_col=mlp.fit(X_train,y_train_col)\\nmlp_sb=mlp.fit(X_train,y_train_sb)\\n\\nsvm_row=svm_single.fit(X_train,y_train_row)\\nsvm_col=svm_single.fit(X_train,y_train_col)\\nsvm_sb=svm_single.fit(X_train,y_train_sb)\\n\\n\\nfor i in range(3):\\n    if max(false_pass_count)==false_pass_count[i]:\\n        if i==1:\\n            dt2=eval(\"RandomForestClassifier(bootstrap=True, class_weight=None, criterion=\\'entropy\\',            max_depth=%s, max_features=\\'auto\\', max_leaf_nodes=None,            min_impurity_decrease=%s, min_impurity_split=None,            min_samples_leaf=1, min_samples_split=2,            min_weight_fraction_leaf=%s, n_estimators=50, n_jobs=None,            oob_score=False, random_state=0, verbose=0, warm_start=False)\" % (best_depth,best_impurity_decrease,best_weight_fraction_leaf) )\\n            dt_row2=dt2.fit(X_train,y_train_row)\\n            dt_col2=dt2.fit(X_train,y_train_col)\\n            dt_sb2=dt2.fit(X_train,y_train_sb)\\n            dt_row=dt.fit(X_train,y_train_row)\\n            dt_col=dt.fit(X_train,y_train_col)\\n            dt_sb=dt.fit(X_train,y_train_sb)            \\n            \\n            if dt_row2.score(X_test,y_test_row)>dt_row.score(X_test,y_test_row):\\n                if dt_col2.score(X_test,y_test_col)>dt_col.score(X_test,y_test_col):\\n                    if dt_sb2.score(X_test,y_test_sb)>dt_sb.score(X_test,y_test_sb):\\n                        print(\"changed dt\")\\n                        dt=dt2\\n                        dt.fit(X_train,y_train)\\n            dt_row=dt.fit(X_train,y_train_row)\\n            dt_col=dt.fit(X_train,y_train_col)\\n            dt_sb=dt.fit(X_train,y_train_sb)\\n        elif i==2:\\n            svm2=BaggingClassifier(base_estimator=svm, n_estimators=10)\\n            svm_row2=svm2.fit(X_train,y_train_row)\\n            svm_col2=svm2.fit(X_train,y_train_col)\\n            svm_sb2=svm2.fit(X_train,y_train_sb)\\n            svm_row=svm_single.fit(X_train,y_train_row)\\n            svm_col=svm_single.fit(X_train,y_train_col)\\n            svm_sb=svm_single.fit(X_train,y_train_sb)            \\n            if svm_row2.score(X_test,y_test_row)>svm_row.score(X_test,y_test_row):\\n                if svm_col2.score(X_test,y_test_col)>svm_col.score(X_test,y_test_col):\\n                    if svm_sb2.score(X_test,y_test_sb)>svm_sb.score(X_test,y_test_sb):\\n                        print(\"changed svm\")\\n                        svm=svm2         \\n            svm_row=svm.fit(X_train,y_train_row)\\n            svm_col=svm.fit(X_train,y_train_col)\\n            svm_sb=svm.fit(X_train,y_train_sb)\\n                        \\n        elif i==3:\\n            mlp2=BaggingClassifier(base_estimator=mlp, n_estimators=10)\\n            mlp_row2=mlp2.fit(X_train,y_train_row)\\n            mlp_col2=mlp2.fit(X_train,y_train_col)\\n            mlp_sb2=mlp2.fit(X_train,y_train_sb)\\n            mlp_row=mlp.fit(X_train,y_train_row)\\n            mlp_col=mlp.fit(X_train,y_train_col)\\n            mlp_sb=mlp.fit(X_train,y_train_sb)\\n            if mlp_row2.score(X_test,y_test_row)>mlp_row.score(X_test,y_test):\\n                if mlp_col2.score(X_test,y_test_col)>mlp_col.score(X_test,y_test):\\n                    if mlp_sb2.score(X_test,y_test_sb)>mlp_sb.score(X_test,y_test):\\n                        print(\"changed mlp\")\\n                        mlp=mlp2\\n                        #mlp.fit(X_train,y_train)            \\n            mlp_row=mlp.fit(X_train,y_train_row)\\n            mlp_col=mlp.fit(X_train,y_train_col)\\n            mlp_sb=mlp.fit(X_train,y_train_sb)\\n        break\\n\\nprint(dt)\\nprint(svm)\\nprint(mlp)\\n\\n            \\n\\n\\n#print (mlp_row.predict(X_test))\\n#VoteSysRow=VotingClassifier(estimators=[(\\'first\\', dt_row), (\\'second\\',svm_row ),(\\'third\\',mlp_row) ], voting=\\'soft\\')\\nVoteSysRow=VotingClassifier(estimators=[(\\'first\\', dt_row), (\\'second\\',svm_row ),(\\'third\\',mlp_row) ], voting=\\'soft\\')\\n\\n\\n\\nprint(\"%s\" % VoteSysRow)\\n#print(y_test_row)\\nVoteSysRow=VoteSysRow.fit(X_train, y_train_row)\\n\\n\\nFinalPred = VoteSysRow.predict(X_test)\\n  \\n          \\n\\n\\nFinalPredProba = VoteSysRow.predict_proba(X_test)\\nprint(confusion_matrix(y_test_row,FinalPred))  \\nprint(classification_report(y_test_row,FinalPred)) \\n\\nprint(VoteSysRow.score(X_test,y_test_row))  \\n\\n\\nraise\\n'"
      ]
     },
     "execution_count": 42,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "#Debugging purpose. Ignored\n",
    "from sklearn.ensemble import VotingClassifier,BaggingClassifier\n",
    "from sklearn.neural_network import MLPClassifier\n",
    "\n",
    "'''\n",
    "mlp=MLPClassifier(activation='logistic', alpha=0.9920073082747223,\n",
    "              batch_size='auto', beta_1=0.9, beta_2=0.999, early_stopping=True,\n",
    "              epsilon=1e-08)\n",
    "mlp.fit(X_train, y_train)\n",
    "print(mlp)\n",
    "\n",
    "#print(dt.predict(X_test))\n",
    "\n",
    "print(svm)\n",
    "\n",
    "#print(svm.predict(X_test))\n",
    "#Extracting ROW/COL/SB y and predict result from multilabel array as sklearn metrics may not support multilabel for bagging classifier.\n",
    "y_train_row=[]\n",
    "y_test_row=[]\n",
    "dt_pred_row=[]\n",
    "svm_pred_row=[]\n",
    "mlp_pred_row=[]\n",
    "for elem in y_train:\n",
    "    y_train_row.append(elem[0])\n",
    "for elem in y_test:    \n",
    "    y_test_row.append(elem[0])\n",
    "for elem in dt.predict(X_test):    \n",
    "    dt_pred_row.append(elem[0])\n",
    "for elem in svm.predict(X_test):    \n",
    "    svm_pred_row.append(elem[0])\n",
    "for elem in mlp.predict(X_test):    \n",
    "    mlp_pred_row.append(elem[0])\n",
    "    \n",
    "y_train_col=[]\n",
    "y_test_col=[]\n",
    "dt_pred_col=[]\n",
    "svm_pred_col=[]\n",
    "mlp_pred_col=[]\n",
    "for elem in y_train:\n",
    "    y_train_col.append(elem[1])\n",
    "for elem in y_test:    \n",
    "    y_test_col.append(elem[1])\n",
    "for elem in dt.predict(X_test):    \n",
    "    dt_pred_col.append(elem[1])\n",
    "for elem in svm.predict(X_test):    \n",
    "    svm_pred_col.append(elem[1])\n",
    "for elem in mlp.predict(X_test):    \n",
    "    mlp_pred_col.append(elem[1])\n",
    "    \n",
    "y_train_sb=[]\n",
    "y_test_sb=[]\n",
    "dt_pred_sb=[]\n",
    "svm_pred_sb=[]\n",
    "mlp_pred_sb=[]\n",
    "for elem in y_train:\n",
    "    y_train_sb.append(elem[2])\n",
    "for elem in y_test:    \n",
    "    y_test_sb.append(elem[2])\n",
    "for elem in dt.predict(X_test):    \n",
    "    dt_pred_sb.append(elem[2])\n",
    "for elem in svm.predict(X_test):    \n",
    "    svm_pred_sb.append(elem[2])\n",
    "for elem in mlp.predict(X_test):    \n",
    "    mlp_pred_sb.append(elem[2])\n",
    "        \n",
    "#print(y_train_row)\n",
    "false_pass_count=[\n",
    "    confusion_matrix(y_test_row,dt_pred_row )[1][0] + confusion_matrix(y_test_col,dt_pred_col )[1][0] + confusion_matrix(y_test_sb,dt_pred_sb )[1][0],\n",
    "    confusion_matrix(y_test_row,svm_pred_row )[1][0] + confusion_matrix(y_test_col,svm_pred_col )[1][0] + confusion_matrix(y_test_sb,svm_pred_sb )[1][0],\n",
    "    confusion_matrix(y_test_row,mlp_pred_row ) [1][0] + confusion_matrix(y_test_col,mlp_pred_col )[1][0] + confusion_matrix(y_test_sb,mlp_pred_sb )[1][0]\n",
    "]\n",
    "\n",
    "#print(false_pass_count[0])\n",
    "    \n",
    "\n",
    "dt_row=dt.fit(X_train,y_train_row)\n",
    "dt_col=dt.fit(X_train,y_train_col)\n",
    "dt_sb=dt.fit(X_train,y_train_sb)\n",
    "\n",
    "\n",
    "mlp_row=mlp.fit(X_train,y_train_row)\n",
    "mlp_col=mlp.fit(X_train,y_train_col)\n",
    "mlp_sb=mlp.fit(X_train,y_train_sb)\n",
    "\n",
    "svm_row=svm_single.fit(X_train,y_train_row)\n",
    "svm_col=svm_single.fit(X_train,y_train_col)\n",
    "svm_sb=svm_single.fit(X_train,y_train_sb)\n",
    "\n",
    "\n",
    "for i in range(3):\n",
    "    if max(false_pass_count)==false_pass_count[i]:\n",
    "        if i==1:\n",
    "            dt2=eval(\"RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',\\\n",
    "            max_depth=%s, max_features='auto', max_leaf_nodes=None,\\\n",
    "            min_impurity_decrease=%s, min_impurity_split=None,\\\n",
    "            min_samples_leaf=1, min_samples_split=2,\\\n",
    "            min_weight_fraction_leaf=%s, n_estimators=50, n_jobs=None,\\\n",
    "            oob_score=False, random_state=0, verbose=0, warm_start=False)\" % (best_depth,best_impurity_decrease,best_weight_fraction_leaf) )\n",
    "            dt_row2=dt2.fit(X_train,y_train_row)\n",
    "            dt_col2=dt2.fit(X_train,y_train_col)\n",
    "            dt_sb2=dt2.fit(X_train,y_train_sb)\n",
    "            dt_row=dt.fit(X_train,y_train_row)\n",
    "            dt_col=dt.fit(X_train,y_train_col)\n",
    "            dt_sb=dt.fit(X_train,y_train_sb)            \n",
    "            \n",
    "            if dt_row2.score(X_test,y_test_row)>dt_row.score(X_test,y_test_row):\n",
    "                if dt_col2.score(X_test,y_test_col)>dt_col.score(X_test,y_test_col):\n",
    "                    if dt_sb2.score(X_test,y_test_sb)>dt_sb.score(X_test,y_test_sb):\n",
    "                        print(\"changed dt\")\n",
    "                        dt=dt2\n",
    "                        dt.fit(X_train,y_train)\n",
    "            dt_row=dt.fit(X_train,y_train_row)\n",
    "            dt_col=dt.fit(X_train,y_train_col)\n",
    "            dt_sb=dt.fit(X_train,y_train_sb)\n",
    "        elif i==2:\n",
    "            svm2=BaggingClassifier(base_estimator=svm, n_estimators=10)\n",
    "            svm_row2=svm2.fit(X_train,y_train_row)\n",
    "            svm_col2=svm2.fit(X_train,y_train_col)\n",
    "            svm_sb2=svm2.fit(X_train,y_train_sb)\n",
    "            svm_row=svm_single.fit(X_train,y_train_row)\n",
    "            svm_col=svm_single.fit(X_train,y_train_col)\n",
    "            svm_sb=svm_single.fit(X_train,y_train_sb)            \n",
    "            if svm_row2.score(X_test,y_test_row)>svm_row.score(X_test,y_test_row):\n",
    "                if svm_col2.score(X_test,y_test_col)>svm_col.score(X_test,y_test_col):\n",
    "                    if svm_sb2.score(X_test,y_test_sb)>svm_sb.score(X_test,y_test_sb):\n",
    "                        print(\"changed svm\")\n",
    "                        svm=svm2         \n",
    "            svm_row=svm.fit(X_train,y_train_row)\n",
    "            svm_col=svm.fit(X_train,y_train_col)\n",
    "            svm_sb=svm.fit(X_train,y_train_sb)\n",
    "                        \n",
    "        elif i==3:\n",
    "            mlp2=BaggingClassifier(base_estimator=mlp, n_estimators=10)\n",
    "            mlp_row2=mlp2.fit(X_train,y_train_row)\n",
    "            mlp_col2=mlp2.fit(X_train,y_train_col)\n",
    "            mlp_sb2=mlp2.fit(X_train,y_train_sb)\n",
    "            mlp_row=mlp.fit(X_train,y_train_row)\n",
    "            mlp_col=mlp.fit(X_train,y_train_col)\n",
    "            mlp_sb=mlp.fit(X_train,y_train_sb)\n",
    "            if mlp_row2.score(X_test,y_test_row)>mlp_row.score(X_test,y_test):\n",
    "                if mlp_col2.score(X_test,y_test_col)>mlp_col.score(X_test,y_test):\n",
    "                    if mlp_sb2.score(X_test,y_test_sb)>mlp_sb.score(X_test,y_test):\n",
    "                        print(\"changed mlp\")\n",
    "                        mlp=mlp2\n",
    "                        #mlp.fit(X_train,y_train)            \n",
    "            mlp_row=mlp.fit(X_train,y_train_row)\n",
    "            mlp_col=mlp.fit(X_train,y_train_col)\n",
    "            mlp_sb=mlp.fit(X_train,y_train_sb)\n",
    "        break\n",
    "\n",
    "print(dt)\n",
    "print(svm)\n",
    "print(mlp)\n",
    "\n",
    "            \n",
    "\n",
    "\n",
    "#print (mlp_row.predict(X_test))\n",
    "#VoteSysRow=VotingClassifier(estimators=[('first', dt_row), ('second',svm_row ),('third',mlp_row) ], voting='soft')\n",
    "VoteSysRow=VotingClassifier(estimators=[('first', dt_row), ('second',svm_row ),('third',mlp_row) ], voting='soft')\n",
    "\n",
    "\n",
    "\n",
    "print(\"%s\" % VoteSysRow)\n",
    "#print(y_test_row)\n",
    "VoteSysRow=VoteSysRow.fit(X_train, y_train_row)\n",
    "\n",
    "\n",
    "FinalPred = VoteSysRow.predict(X_test)\n",
    "  \n",
    "          \n",
    "\n",
    "\n",
    "FinalPredProba = VoteSysRow.predict_proba(X_test)\n",
    "print(confusion_matrix(y_test_row,FinalPred))  \n",
    "print(classification_report(y_test_row,FinalPred)) \n",
    "\n",
    "print(VoteSysRow.score(X_test,y_test_row))  \n",
    "\n",
    "\n",
    "raise\n",
    "'''\n",
    "                           \n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 43,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 3: MLP"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 44,
   "metadata": {},
   "outputs": [
    {
     "ename": "ModuleNotFoundError",
     "evalue": "No module named 'seaborn'",
     "output_type": "error",
     "traceback": [
      "\u001b[1;31m---------------------------------------------------------------------------\u001b[0m",
      "\u001b[1;31mModuleNotFoundError\u001b[0m                       Traceback (most recent call last)",
      "\u001b[1;32m<ipython-input-44-862b56dc3eee>\u001b[0m in \u001b[0;36m<module>\u001b[1;34m\u001b[0m\n\u001b[0;32m      7\u001b[0m \u001b[1;32mfrom\u001b[0m \u001b[0mitertools\u001b[0m \u001b[1;32mimport\u001b[0m \u001b[0mcycle\u001b[0m\u001b[1;33m,\u001b[0m \u001b[0mproduct\u001b[0m\u001b[1;33m\u001b[0m\u001b[1;33m\u001b[0m\u001b[0m\n\u001b[0;32m      8\u001b[0m \u001b[1;32mfrom\u001b[0m \u001b[0msklearn\u001b[0m\u001b[1;33m.\u001b[0m\u001b[0mmanifold\u001b[0m \u001b[1;32mimport\u001b[0m \u001b[0mTSNE\u001b[0m\u001b[1;33m\u001b[0m\u001b[1;33m\u001b[0m\u001b[0m\n\u001b[1;32m----> 9\u001b[1;33m \u001b[1;32mimport\u001b[0m \u001b[0mseaborn\u001b[0m \u001b[1;32mas\u001b[0m \u001b[0msns\u001b[0m\u001b[1;33m\u001b[0m\u001b[1;33m\u001b[0m\u001b[0m\n\u001b[0m\u001b[0;32m     10\u001b[0m \u001b[1;32mfrom\u001b[0m \u001b[0mhyperopt\u001b[0m \u001b[1;32mimport\u001b[0m \u001b[0mfmin\u001b[0m\u001b[1;33m,\u001b[0m \u001b[0mtpe\u001b[0m\u001b[1;33m,\u001b[0m \u001b[0mhp\u001b[0m\u001b[1;33m,\u001b[0m \u001b[0mSTATUS_OK\u001b[0m\u001b[1;33m,\u001b[0m \u001b[0mTrials\u001b[0m\u001b[1;33m\u001b[0m\u001b[1;33m\u001b[0m\u001b[0m\n\u001b[0;32m     11\u001b[0m \u001b[1;32mimport\u001b[0m \u001b[0mhyperopt\u001b[0m\u001b[1;33m.\u001b[0m\u001b[0mpyll\u001b[0m\u001b[1;33m.\u001b[0m\u001b[0mstochastic\u001b[0m\u001b[1;33m\u001b[0m\u001b[1;33m\u001b[0m\u001b[0m\n",
      "\u001b[1;31mModuleNotFoundError\u001b[0m: No module named 'seaborn'"
     ]
    }
   ],
   "source": [
    "from sklearn.model_selection import train_test_split, cross_val_score, RandomizedSearchCV\n",
    "from sklearn.neural_network import MLPClassifier\n",
    "from sklearn.metrics import classification_report, multilabel_confusion_matrix\n",
    "import eli5\n",
    "from eli5.sklearn import PermutationImportance\n",
    "from sklearn.multiclass import OneVsRestClassifier, _fit_binary\n",
    "from itertools import cycle, product\n",
    "from sklearn.manifold import TSNE\n",
    "import seaborn as sns\n",
    "from hyperopt import fmin, tpe, hp, STATUS_OK, Trials\n",
    "import hyperopt.pyll.stochastic\n",
    "import time\n",
    "#from sklearn.externals.joblib import Parallel, delayed\n",
    "from sklearn.ensemble import VotingClassifier\n",
    "from joblib import Parallel, delayed\n",
    "\n",
    "#Section 3.0 data preprossing\n",
    "\n",
    "# Reading the data\n",
    "failure = pd.read_csv('TargetData.csv')\n",
    "\n",
    "# Inspecting the data\n",
    "pd.options.display.max_rows = 1000\n",
    "print(failure.shape)\n",
    "print(failure.head(3).transpose()) # 3093 data points with 1 ID, 58 features and 5 targets\n",
    "print(failure.describe().transpose()) # 3 features do not have any variance: 'gallop 1','gallop 5','Row Shift 7'\n",
    "\n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "# Set up the data and label\n",
    "#X consists of 58 features. Each feature represents 1 test in the long test flow.\n",
    "X = failure.drop(['ID', 'gallop 1', 'gallop 5', 'Row Shift 7', 'SB','COL', 'Margin', 'Block', 'ROW'], axis=1)\n",
    "#Y can be one of ROW,COL,SB. ROW means the failure is on a row of memory array.\n",
    "#COL means the failure is on a column of the cell array\n",
    "#SB is single bit failure inside the memory\n",
    "#Forming 8 class from 3 columns, coded as 0 to 7\n",
    "#['Overkill','SB','COL','SB+COL','ROW','ROW+SB','ROW+COL','SB+ROW+COL']\n",
    "  #y = failure.SB+2*failure.COL+4*failure.ROW\n",
    "\n",
    "#Converting y to reflect multilabels\n",
    "  #mlb = MultiLabelBinarizer()\n",
    "  #y_converted = mlb.fit_transform(failure[['SB','COL','ROW']])\n",
    "\n",
    "target = ['multilabels', 'SB', 'ROW', 'COL']\n",
    "y = [None] * len(target)\n",
    "\n",
    "y[0] = failure[['SB', 'ROW', 'COL']].values\n",
    "n_classes = y[0].shape[1]\n",
    "\n",
    "for (i, j) in zip(range(1, len(target)), ['SB', 'ROW', 'COL']):\n",
    "    y[i] = failure[j].values\n",
    "    \n",
    "    "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 3.1 t-SNE model\n",
    "# Runnig the t-SNE model\n",
    "i = ['SB', 'ROW', 'COL'] \n",
    "\n",
    "for i in i:\n",
    "    failure[i] = failure[i].replace({0: 'Negative', 1: 'Positive'})\n",
    "\n",
    "# Create a t-SNE model with learning rate 50\n",
    "embedding = TSNE(n_components=2,\n",
    "                 perplexity=30,\n",
    "                 learning_rate=200.0,\n",
    "                 verbose=10,\n",
    "                 random_state=42)\n",
    "\n",
    "# Fit and transform the t-SNE model on the numeric dataset\n",
    "tsne_features = pd.DataFrame(embedding.fit_transform(X))\n",
    "\n",
    "tsne_features_failure = tsne_features.join([failure['SB'], failure['ROW'], failure['COL']])\n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "# Color the points according to types of failure\n",
    "sns.set(rc={'figure.figsize': (25,25), 'legend.fontsize': 25, 'xtick.labelsize': 25, 'ytick.labelsize': 25, \n",
    "            'lines.markersize': 12.5, 'axes.labelsize': 0, 'axes.titlesize': 24})\n",
    "\n",
    "fig, ax = plt.subplots(3,1)\n",
    "\n",
    "j = ['SB', 'ROW', 'COL']\n",
    "k = ['Reds', 'Purples', 'Greens']\n",
    "l = ['darkred', 'violet', 'darkgreen']\n",
    "\n",
    "for (i, j, k, l) in zip(range(n_classes), j, k, l):\n",
    "    \n",
    "    ax[i].set_title('t-SNE Plot of {}'.format(j))\n",
    "    \n",
    "    sns.kdeplot(data=tsne_features_failure[tsne_features_failure[j] == 'Positive'][0],\n",
    "                data2=tsne_features_failure[tsne_features_failure[j] == 'Positive'][1],\n",
    "                cmap=k,\n",
    "                shade=True,\n",
    "                bw=3,\n",
    "                cbar=True, \n",
    "                ax=ax[i])\n",
    "    \n",
    "    sns.scatterplot(x=tsne_features_failure[0],\n",
    "                    y=tsne_features_failure[1],\n",
    "                    hue=tsne_features_failure[j],\n",
    "                    style=tsne_features_failure[j],\n",
    "                    palette=['aqua', l],\n",
    "                    alpha=0.05,\n",
    "                    ax=ax[i])\n",
    "    "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "# Section 3.2 Building MLP\n",
    "# Train/test split\n",
    "y_train = [None] * len(target)\n",
    "y_test = [None] * len(target)\n",
    "\n",
    "for i in range(len(target)):\n",
    "    X_train, X_test, y_train[i], y_test[i] = train_test_split(X, y[i],\n",
    "                                                              test_size=1/3,\n",
    "                                                              random_state=42,\n",
    "                                                              stratify=y[0])\n",
    "    \n",
    "# Set up space dictionary with specified hyperparameters\n",
    "space = {'hidden_layer_sizes': hp.choice('hidden_layer_sizes', range(1,56)),\n",
    "         'activation': hp.choice('activation', ['logistic','tanh','relu', 'identity']),\n",
    "         'solver': hp.choice('solver', ['lbfgs','sgd','adam']),\n",
    "         'alpha': hp.uniform('alpha', 0.0001, 1000),\n",
    "         'learning_rate': hp.choice('learning_rate', ['constant', 'invscaling', 'adaptive']),\n",
    "         'learning_rate_init': hp.uniform('learning_rate_init', 0.001, 0.99),\n",
    "         'power_t': hp.uniform('power_t', 0.01, 0.99)}\n",
    "\n",
    "wave = -1\n",
    "\n",
    "target_clf = [None] * len(target)\n",
    "target_clf_fitted = [None] * len(target)\n",
    "target_y_pred_proba = [None] * len(target)\n",
    "target_y_pred = [None] * len(target)\n",
    "\n",
    "for i in range(len(target)):\n",
    "    target_clf[i] = [None] * 12\n",
    "    target_clf_fitted[i] = [None] * 12\n",
    "    target_y_pred_proba[i] = [None] * 12\n",
    "    target_y_pred[i] = [None] * 12\n",
    "\n",
    "for (i, j) in zip(range(len(target)), ['multilabels', 'SB', 'ROW', 'COL']):\n",
    "    \n",
    "    wave = wave + 1\n",
    "    \n",
    "    # Set up objective function\n",
    "    def objective(params):\n",
    "        params = {'hidden_layer_sizes': params['hidden_layer_sizes'],\n",
    "                  'activation': params['activation'],\n",
    "                  'solver': params['solver'],\n",
    "                  'alpha': params['alpha'],\n",
    "                  'learning_rate': params['learning_rate'],\n",
    "                  'learning_rate_init': params['learning_rate_init'],\n",
    "                  'power_t': params['power_t']}\n",
    "        \n",
    "        hyperopt_clf = MLPClassifier(max_iter=4000,\n",
    "                                     random_state=42,\n",
    "                                     warm_start=True,\n",
    "                                     early_stopping=True,\n",
    "                                     **params)\n",
    "\n",
    "        best_score = cross_val_score(estimator=hyperopt_clf,\n",
    "                                     X=X_train,\n",
    "                                     y=y_train[i],\n",
    "                                     cv=3,\n",
    "                                     n_jobs=4,\n",
    "                                     pre_dispatch=10).mean()\n",
    "    \n",
    "        loss = 1 - best_score\n",
    "        return {'best_score': best_score, 'loss': loss, 'status': STATUS_OK,'eval_time': time.time()}\n",
    "\n",
    "    # Run the algorithm\n",
    "    trials = Trials()\n",
    "    best = fmin(fn=objective,\n",
    "           space=space,\n",
    "           max_evals=100,\n",
    "           rstate=np.random.RandomState(42),\n",
    "           algo=tpe.suggest,\n",
    "           trials=trials)\n",
    "    \n",
    "    print('{}----------'.format(j))\n",
    "    \n",
    "    best_score = [None] * len(trials.trials)\n",
    "    best_score[0] = trials.results[0].get('best_score')\n",
    "\n",
    "    searched_params_df = pd.DataFrame(trials.trials[0].get('misc').get('vals').values())\n",
    "    searched_params_df = searched_params_df.transpose()\n",
    "\n",
    "    for i in list(range(1, len(trials.trials))):\n",
    "        new_df = pd.DataFrame(trials.trials[i].get('misc').get('vals').values())\n",
    "        searched_params_df = searched_params_df.append(new_df.transpose())\n",
    "        best_score[i] = trials.results[i].get('best_score')\n",
    "\n",
    "    searched_params_df = searched_params_df.rename(columns={0: 'activation', 1: 'alpha', 2: 'hidden_layer_sizes', \n",
    "                                                            3: 'learning_rate', 4: 'learning_rate_init', \n",
    "                                                            5: 'power_t', 6: 'solver'})\n",
    "    \n",
    "    blankIndex = [''] * len(searched_params_df)\n",
    "    searched_params_df.index = blankIndex\n",
    "    \n",
    "    i = ['activation', 'learning_rate', 'solver']\n",
    "    j = ['logistic', 'constant', 'lbfgs']\n",
    "    k = ['tanh', 'invscaling', 'sgd']\n",
    "    l = ['relu', 'adaptive', 'adam']\n",
    "    m = ['identity']\n",
    "\n",
    "    for (i, j, k, l) in zip(i, j, k, l):\n",
    "         searched_params_df[i] = searched_params_df[i].replace({0: j, 1: k, 2: l, 3: m})\n",
    "\n",
    "    searched_params_df['best_score'] = best_score\n",
    "\n",
    "    searched_params_df_sorted = searched_params_df.sort_values(by='best_score', \n",
    "                                                               axis=0, \n",
    "                                                               ascending=False)\n",
    "    \n",
    "    searched_params_df_sorted = searched_params_df_sorted[searched_params_df_sorted.hidden_layer_sizes != 0]\n",
    "\n",
    "    print(searched_params_df_sorted.head(5).transpose())\n",
    "    print('__________')\n",
    "    \n",
    "    # Learn to predict each class against the other\n",
    "        \n",
    "    for i in range(5):\n",
    "        target_clf[wave][i] = MLPClassifier(max_iter=4000,\n",
    "                                            random_state=42,\n",
    "                                            warm_start=True,\n",
    "                                            early_stopping=True,\n",
    "                                            activation=searched_params_df_sorted.values[i][0],\n",
    "                                            alpha=searched_params_df_sorted.values[i][1],\n",
    "                                            hidden_layer_sizes=int(searched_params_df_sorted.values[i][2]),\n",
    "                                            learning_rate=searched_params_df_sorted.values[i][3],\n",
    "                                            learning_rate_init=searched_params_df_sorted.values[i][4],\n",
    "                                            power_t=searched_params_df_sorted.values[i][5],\n",
    "                                            solver=searched_params_df_sorted.values[i][6])\n",
    "    \n",
    "    if wave == 0:\n",
    "        for i in range(5):\n",
    "            target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])\n",
    "            target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)\n",
    "            target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)\n",
    "    else:\n",
    "        # Create and fit the voting classifier\n",
    "        target_clf[wave][5] = VotingClassifier(estimators=[('first', target_clf[wave][0]), \n",
    "                                                           ('second', target_clf[wave][1]), \n",
    "                                                           ('third', target_clf[wave][2]), \n",
    "                                                           ('forth', target_clf[wave][3]),\n",
    "                                                           ('fifth', target_clf[wave][4])],\n",
    "                                                voting='soft',\n",
    "                                                n_jobs=4)\n",
    "    \n",
    "        for i in range(6):\n",
    "            target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])\n",
    "            target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)\n",
    "            target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)\n",
    "\n",
    "    # Create the parameter grid\n",
    "    ##param_grid = {'hidden_layer_sizes': list(product(range(1,56), range(1,56)))}\n",
    "    \n",
    "    # Create a random search object\n",
    "    ##ran_clf = RandomizedSearchCV(estimator = MLPClassifier(max_iter=4000,\n",
    "                                                           ##random_state=42,\n",
    "                                                           ##warm_start=True,\n",
    "                                                           ##early_stopping=True,\n",
    "                                                           ##activation=searched_params_df_sorted.values[0][0],\n",
    "                                                           ##alpha=searched_params_df_sorted.values[0][1],\n",
    "                                                           ##learning_rate=searched_params_df_sorted.values[0][3],\n",
    "                                                           ##learning_rate_init=searched_params_df_sorted.values[0][4],\n",
    "                                                           ##power_t=searched_params_df_sorted.values[0][5],\n",
    "                                                           ##solver=searched_params_df_sorted.values[0][6]),\n",
    "                                 ##param_distributions=param_grid,\n",
    "                                 ##n_iter=465,\n",
    "                                 ##n_jobs=4,\n",
    "                                 ##pre_dispatch=100,\n",
    "                                 ##cv=3,\n",
    "                                 ##random_state=42)\n",
    "\n",
    "    ##ran_clf_fitted = ran_clf.fit(X_train, y_train[wave])\n",
    "\n",
    "    #Configuration of Layer 1 & 2\n",
    "    ##mean_test_score = list(ran_clf_fitted.cv_results_.get('mean_test_score'))\n",
    "    ##hidden_layers = list(ran_clf_fitted.cv_results_.get('param_hidden_layer_sizes'))\n",
    "\n",
    "    ##best_hidden_layers_df = pd.DataFrame({'Hidden Layers': hidden_layers, 'Mean Test Score': mean_test_score})\n",
    "\n",
    "    ##blankIndex = [''] * len(best_hidden_layers_df)\n",
    "    ##best_hidden_layers_df.index = blankIndex\n",
    "\n",
    "    # Print out the best configuration of hidden layers\n",
    "    ##best_hidden_layers_df_sorted = best_hidden_layers_df.sort_values(by='Mean Test Score', \n",
    "                                                                     ##axis=0, \n",
    "                                                                     ##ascending=False)\n",
    "\n",
    "    ##print(best_hidden_layers_df_sorted.head(5).transpose())\n",
    "    ##print()\n",
    "\n",
    "    ##for i in range(6, 11):\n",
    "        ##target_clf[wave][i] = MLPClassifier(max_iter=4000,\n",
    "                                            ##random_state=42,\n",
    "                                            ##warm_start=True,\n",
    "                                            ##early_stopping=True,\n",
    "                                            ##activation=searched_params_df_sorted.values[0][0],\n",
    "                                            ##alpha=searched_params_df_sorted.values[0][1],\n",
    "                                            ##hidden_layer_sizes=best_hidden_layers_df_sorted['Hidden Layers'].values[i-6],\n",
    "                                            ##learning_rate=searched_params_df_sorted.values[0][3],\n",
    "                                            ##learning_rate_init=searched_params_df_sorted.values[0][4],\n",
    "                                            ##power_t=searched_params_df_sorted.values[0][5],\n",
    "                                            ##solver=searched_params_df_sorted.values[0][6])\n",
    "    \n",
    "    ##if wave == 0:\n",
    "        ##for i in range(6, 11):\n",
    "            ##target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])\n",
    "            ##target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)\n",
    "            ##target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)\n",
    "    ##else:\n",
    "        # Create and fit the voting classifier\n",
    "        ##target_clf[wave][11] = VotingClassifier(estimators=[('first', target_clf[wave][6]), \n",
    "                                                            ##('second', target_clf[wave][7]), \n",
    "                                                            ##('third', target_clf[wave][8]), \n",
    "                                                            ##('forth', target_clf[wave][9]),\n",
    "                                                            ##('fifth', target_clf[wave][10])],\n",
    "                                                ##voting='soft',\n",
    "                                                ##n_jobs=4)\n",
    "    \n",
    "        ##for i in range(6, 12):\n",
    "            ##target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])\n",
    "            ##target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)\n",
    "            ##target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)\n",
    "    \n",
    "    #sns.set(rc={'figure.figsize': (20,20), 'legend.fontsize': 25, 'xtick.labelsize': 20, 'ytick.labelsize': 20, \n",
    "            #'lines.markersize': 10, 'axes.labelsize': 20, 'axes.titlesize': 20})\n",
    "\n",
    "    #first_hidden_layer = [None] * len(hidden_layers)\n",
    "    #second_hidden_layer = [None] * len(hidden_layers)\n",
    "\n",
    "    #for i in range(len(hidden_layers)):\n",
    "        #first_hidden_layer[i] = hidden_layers[i][0]\n",
    "        #second_hidden_layer[i] = hidden_layers[i][1]\n",
    "\n",
    "    #ax = sns.scatterplot(x=first_hidden_layer,\n",
    "                         #y=second_hidden_layer)\n",
    "    #ax.set_title('Scatterplot of the Combination of the Number of Neurons in the First & Second Hidden Layers')\n",
    " \n",
    "    # Color the points according to types of failure\n",
    "    sns.set(rc={'figure.figsize': (35,40), 'legend.fontsize': 25, 'xtick.labelsize': 20, 'ytick.labelsize': 20, \n",
    "                'lines.markersize': 10, 'axes.labelsize': 0, 'axes.titlesize': 20})\n",
    "\n",
    "    fig, ax = plt.subplots(7,1)\n",
    "\n",
    "    j = ['Activation Function for the Hidden Layer', 'L2 Penalty', 'Number of Neurons', \n",
    "         'Learning Rate Schedule for Weight Updates', 'Initial Learning Rate', 'Exponent for Inverse Scaling Learning Rate',\n",
    "         'Solver for Weight Optimization']\n",
    "    k = ['activation', 'alpha', 'hidden_layer_sizes', 'learning_rate', 'learning_rate_init', 'power_t', 'solver']\n",
    "    \n",
    "    for (i, j, k) in zip(range(7), j, k):\n",
    "    \n",
    "        ax[i].set_title('{}---Searched Parameters of the {}'.format(target[wave], j))\n",
    "        sns.scatterplot(x=list(range(0, len(trials.trials))), \n",
    "                        y=searched_params_df[k].values, \n",
    "                        ax=ax[i])\n",
    "        \n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "# Print classification report\n",
    "wave = -1\n",
    "\n",
    "for (i, j) in zip(range(len(target)), ['multilabels', 'SB', 'ROW', 'COL']):\n",
    "    wave = wave + 1\n",
    "    \n",
    "    print(j)\n",
    "    \n",
    "    if wave == 0:\n",
    "        i = [0, 1, 2, 3, 4]\n",
    "        j = ['1stBest_1Layer', '2ndBest_1Layer', '3rdBest_1Layer', '4thBest_1Layer', '5thBest_1Layer']\n",
    "\n",
    "        for (i, j) in zip(i, j):\n",
    "            print('{}----------'.format(j))\n",
    "            print()\n",
    "            print(multilabel_confusion_matrix(y_true=y_test[wave], \n",
    "                                              y_pred=target_y_pred[wave][i]))\n",
    "            print(classification_report(y_true=y_test[wave], \n",
    "                                        y_pred=target_y_pred[wave][i],\n",
    "                                        target_names=['SB', 'ROW', 'COL'],\n",
    "                                        digits=2))\n",
    "    else:\n",
    "        i = [0, 1, 2, 3, 4, 5]\n",
    "        j = ['1stBest_1Layer', '2ndBest_1Layer', '3rdBest_1Layer', '4thBest_1Layer', '5thBest_1Layer', 'CombineBest_1Layer']\n",
    "\n",
    "        for (i, j) in zip(i, j):\n",
    "            print('{}----------'.format(j))\n",
    "            print()\n",
    "            print(confusion_matrix(y_true=y_test[wave], \n",
    "                                   y_pred=target_y_pred[wave][i]))\n",
    "            print(classification_report(y_true=y_test[wave], \n",
    "                                        y_pred=target_y_pred[wave][i],\n",
    "                                        target_names=['NonFault', 'Fault'],\n",
    "                                        digits=2))\n",
    "            "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "# Computing feature importance\n",
    "print('Best MLP estimator: {}'.format(target_clf[0][0]))\n",
    "print()\n",
    "print('Best results')\n",
    "print(multilabel_confusion_matrix(y_true=y_test[0], \n",
    "                                  y_pred=target_y_pred[0][0]))\n",
    "print(classification_report(y_true=y_test[0], \n",
    "                            y_pred=target_y_pred[0][0],\n",
    "                            target_names=['SB', 'ROW', 'COL'],\n",
    "                            digits=2))\n",
    "\n",
    "perm = PermutationImportance(estimator=target_clf[0][0],\n",
    "                             n_iter=100,\n",
    "                             random_state=42).fit(X_test, y_test[0])\n",
    "\n",
    "# Create a dataframe of the variables and feature importances\n",
    "feature_importances_df = pd.DataFrame({'Variable': X.columns, 'Feature_Importances': perm.feature_importances_})\n",
    "\n",
    "# Print out the top 3 positive variables\n",
    "feature_importances_df_sorted = feature_importances_df.sort_values(by='Feature_Importances', \n",
    "                                                                   axis=0, \n",
    "                                                                   ascending=False)\n",
    "print()\n",
    "print(feature_importances_df_sorted)\n",
    "\n",
    "mlp=target_clf[0][0]"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 4: Re-train chance of individual based on competition result."
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "from sklearn.ensemble import VotingClassifier\n",
    "\n",
    "X_train,X_test,y_train,y_test=X_train_b,X_test_b,y_train_b,y_test_b\n",
    "\n",
    "mlp1=eval(\"%s\" % mlp)\n",
    "\n",
    "\n",
    "\n",
    "#print(svm.predict(X_test))\n",
    "#Extracting ROW/COL/SB y and predict result from multilabel array as sklearn metrics may not support multilabel for bagging classifier.\n",
    "y_train_row=[]\n",
    "y_test_row=[]\n",
    "dt_pred_row=[]\n",
    "svm_pred_row=[]\n",
    "for elem in y_train:\n",
    "    y_train_row.append(elem[0])\n",
    "for elem in y_test:    \n",
    "    y_test_row.append(elem[0])\n",
    "for elem in dt.predict(X_test):    \n",
    "    dt_pred_row.append(elem[0])\n",
    "for elem in svm.predict(X_test):    \n",
    "    svm_pred_row.append(elem[0])\n",
    "#for elem in mlp1.predict(X_test):    \n",
    "#    mlp_pred_row.append(elem[0])\n",
    "    \n",
    "y_train_col=[]\n",
    "y_test_col=[]\n",
    "dt_pred_col=[]\n",
    "svm_pred_col=[]\n",
    "for elem in y_train:\n",
    "    y_train_col.append(elem[1])\n",
    "for elem in y_test:    \n",
    "    y_test_col.append(elem[1])\n",
    "for elem in dt.predict(X_test):    \n",
    "    dt_pred_col.append(elem[1])\n",
    "for elem in svm.predict(X_test):    \n",
    "    svm_pred_col.append(elem[1])\n",
    "#for elem in mlp1.predict(X_test):    \n",
    "#    mlp_pred_col.append(elem[1])\n",
    "    \n",
    "y_train_sb=[]\n",
    "y_test_sb=[]\n",
    "dt_pred_sb=[]\n",
    "svm_pred_sb=[]\n",
    "for elem in y_train:\n",
    "    y_train_sb.append(elem[2])\n",
    "for elem in y_test:    \n",
    "    y_test_sb.append(elem[2])\n",
    "for elem in dt.predict(X_test):    \n",
    "    dt_pred_sb.append(elem[2])\n",
    "for elem in svm.predict(X_test):    \n",
    "    svm_pred_sb.append(elem[2])\n",
    "#for elem in mlp1.predict(X_test):    \n",
    "#    mlp_pred_sb.append(elem[2])\n",
    "\n",
    "dt_row=dt.fit(X_train,y_train_row)\n",
    "dt_col=dt.fit(X_train,y_train_col)\n",
    "dt_sb=dt.fit(X_train,y_train_sb)\n",
    "\n",
    "\n",
    "mlp_row=mlp1.fit(X_train,y_train_row)\n",
    "mlp_col=mlp1.fit(X_train,y_train_col)\n",
    "mlp_sb=mlp1.fit(X_train,y_train_sb)\n",
    "\n",
    "mlp_pred_sb=mlp_sb.predict(X_test)\n",
    "mlp_pred_row=mlp_row.predict(X_test)\n",
    "mlp_pred_col=mlp_col.predict(X_test)\n",
    "\n",
    "svm_row=svm_single.fit(X_train,y_train_row)\n",
    "svm_col=svm_single.fit(X_train,y_train_col)\n",
    "svm_sb=svm_single.fit(X_train,y_train_sb)\n",
    "\n",
    "\n",
    "\n",
    "#print(y_train_row)\n",
    "false_pass_count=[\n",
    "    confusion_matrix(y_test_row,dt_pred_row )[1][0] + confusion_matrix(y_test_col,dt_pred_col )[1][0] + confusion_matrix(y_test_sb,dt_pred_sb )[1][0],\n",
    "    confusion_matrix(y_test_row,svm_pred_row )[1][0] + confusion_matrix(y_test_col,svm_pred_col )[1][0] + confusion_matrix(y_test_sb,svm_pred_sb )[1][0],\n",
    "    confusion_matrix(y_test_row,mlp_pred_row ) [1][0] + confusion_matrix(y_test_col,mlp_pred_col )[1][0] + confusion_matrix(y_test_sb,mlp_pred_sb )[1][0]\n",
    "]\n",
    "\n",
    "#print(false_pass_count[0])\n",
    "    \n",
    "\n",
    "for i in range(3):\n",
    "    if max(false_pass_count)==false_pass_count[i]:\n",
    "        if i==1:\n",
    "            dt2=eval(\"RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',\\\n",
    "            max_depth=%s, max_features='auto', max_leaf_nodes=None,\\\n",
    "            min_impurity_decrease=%s, min_impurity_split=None,\\\n",
    "            min_samples_leaf=1, min_samples_split=2,\\\n",
    "            min_weight_fraction_leaf=%s, n_estimators=128, n_jobs=None,\\\n",
    "            oob_score=False, random_state=0, verbose=0, warm_start=False)\" % (best_depth,best_impurity_decrease,best_weight_fraction_leaf) )\n",
    "            dt_row2=dt2.fit(X_train,y_train_row)\n",
    "            dt_col2=dt2.fit(X_train,y_train_col)\n",
    "            dt_sb2=dt2.fit(X_train,y_train_sb)\n",
    "            dt_row=dt.fit(X_train,y_train_row)\n",
    "            dt_col=dt.fit(X_train,y_train_col)\n",
    "            dt_sb=dt.fit(X_train,y_train_sb)            \n",
    "            \n",
    "            if dt_row2.score(X_test,y_test_row)>dt_row.score(X_test,y_test_row):\n",
    "                if dt_col2.score(X_test,y_test_col)>dt_col.score(X_test,y_test_col):\n",
    "                    if dt_sb2.score(X_test,y_test_sb)>dt_sb.score(X_test,y_test_sb):\n",
    "                        print(\"changed dt\")\n",
    "                        dt=dt2\n",
    "                        dt.fit(X_train,y_train)\n",
    "            dt_row=dt.fit(X_train,y_train_row)\n",
    "            dt_col=dt.fit(X_train,y_train_col)\n",
    "            dt_sb=dt.fit(X_train,y_train_sb)\n",
    "        elif i==2:\n",
    "            svm2=BaggingClassifier(base_estimator=svm, n_estimators=10)\n",
    "            svm_row2=svm2.fit(X_train,y_train_row)\n",
    "            svm_col2=svm2.fit(X_train,y_train_col)\n",
    "            svm_sb2=svm2.fit(X_train,y_train_sb)\n",
    "            svm_row=svm_single.fit(X_train,y_train_row)\n",
    "            svm_col=svm_single.fit(X_train,y_train_col)\n",
    "            svm_sb=svm_single.fit(X_train,y_train_sb)            \n",
    "            if svm_row2.score(X_test,y_test_row)>svm_row.score(X_test,y_test_row):\n",
    "                if svm_col2.score(X_test,y_test_col)>svm_col.score(X_test,y_test_col):\n",
    "                    if svm_sb2.score(X_test,y_test_sb)>svm_sb.score(X_test,y_test_sb):\n",
    "                        print(\"changed svm\")\n",
    "                        svm=svm2         \n",
    "            svm_row=svm.fit(X_train,y_train_row)\n",
    "            svm_col=svm.fit(X_train,y_train_col)\n",
    "            svm_sb=svm.fit(X_train,y_train_sb)\n",
    "                        \n",
    "        elif i==3:\n",
    "            mlp2=BaggingClassifier(base_estimator=mlp, n_estimators=10)\n",
    "            mlp_row2=mlp2.fit(X_train,y_train_row)\n",
    "            mlp_col2=mlp2.fit(X_train,y_train_col)\n",
    "            mlp_sb2=mlp2.fit(X_train,y_train_sb)\n",
    "            mlp_row=mlp.fit(X_train,y_train_row)\n",
    "            mlp_col=mlp.fit(X_train,y_train_col)\n",
    "            mlp_sb=mlp.fit(X_train,y_train_sb)\n",
    "            if mlp_row2.score(X_test,y_test_row)>mlp_row.score(X_test,y_test):\n",
    "                if mlp_col2.score(X_test,y_test_col)>mlp_col.score(X_test,y_test):\n",
    "                    if mlp_sb2.score(X_test,y_test_sb)>mlp_sb.score(X_test,y_test):\n",
    "                        print(\"changed mlp\")\n",
    "                        mlp=mlp2\n",
    "                        #mlp.fit(X_train,y_train)            \n",
    "            mlp_row=mlp.fit(X_train,y_train_row)\n",
    "            mlp_col=mlp.fit(X_train,y_train_col)\n",
    "            mlp_sb=mlp.fit(X_train,y_train_sb)\n",
    "        break\n",
    "\n",
    "print(dt)\n",
    "print(svm)\n",
    "print(mlp)\n",
    "\n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "#Section 5: Voting ensemble as final output of the system\n",
    "\n",
    "VoteSysRow=VotingClassifier(estimators=[('first', dt_row), \n",
    "                            ('second',svm_row ) ,                            \n",
    "                            ('third',mlp_row ) \n",
    "                                       ],\n",
    "                                                voting='soft')\n",
    "\n",
    "#print(y_test_row)\n",
    "VoteSysRow=VoteSysRow.fit(X_train, y_train_row)\n",
    "print(VoteSysRow)\n",
    "\n",
    "FinalPred = VoteSysRow.predict(X_test)\n",
    "  \n",
    "          \n",
    "\n",
    "\n",
    "FinalPredProba = VoteSysRow.predict_proba(X_test)\n",
    "print(confusion_matrix(y_test_row,FinalPred))  \n",
    "print(classification_report(y_test_row,FinalPred)) \n",
    "\n",
    "print(VoteSysRow.score(X_test,y_test_row))  \n",
    "\n",
    "                           \n",
    "#X_train,X_test,y_train_col,y_test_col = train_test_split(X,test_data.COL,test_size=1/3,random_state=2, stratify=test_data.COL)\n",
    "\n",
    "\n",
    "dt_col=dt.fit(X_train,y_train_col)\n",
    "svm_col=svm_single.fit(X_train,y_train_col)\n",
    "mlp_col=mlp1.fit(X_train,y_train_col)\n",
    "#print (svm_col.predict(X_test))\n",
    "VoteSyscol=VotingClassifier(estimators=[('first', dt_col), \n",
    "                            ('second',svm_col ) ,                            \n",
    "                            ('third',mlp_col ) \n",
    "                                       ],\n",
    "                                                voting='soft')\n",
    "\n",
    "#print(y_test_col)\n",
    "VoteSyscol=VoteSyscol.fit(X_train, y_train_col)\n",
    "print(VoteSyscol)\n",
    "\n",
    "FinalPred = VoteSyscol.predict(X_test)\n",
    "  \n",
    "          \n",
    "\n",
    "\n",
    "FinalPredProba = VoteSyscol.predict_proba(X_test)\n",
    "print(confusion_matrix(y_test_col,FinalPred))  \n",
    "print(classification_report(y_test_col,FinalPred)) \n",
    "\n",
    "print(VoteSyscol.score(X_test,y_test_col))  \n",
    "\n",
    "#X_train,X_test,y_train_sb,y_test_sb = train_test_split(X,test_data.SB,test_size=1/3,random_state=2, stratify=test_data.SB)\n",
    "\n",
    "\n",
    "dt_sb=dt.fit(X_train,y_train_sb)\n",
    "svm_sb=svm_single.fit(X_train,y_train_sb)\n",
    "mlp_sb=mlp1.fit(X_train,y_train_sb)\n",
    "#print (svm_sb.predict(X_test))\n",
    "VoteSyssb=VotingClassifier(estimators=[('first', dt_sb), \n",
    "                            ('second',svm_sb ) ,                            \n",
    "                            ('third',mlp_sb ) ,\n",
    "                                       ],\n",
    "                                                voting='soft')\n",
    "\n",
    "#print(y_test_sb)\n",
    "VoteSyssb=VoteSyssb.fit(X_train, y_train_sb)\n",
    "print(VoteSyssb)\n",
    "\n",
    "FinalPred = VoteSyssb.predict(X_test)\n",
    "  \n",
    "          \n",
    "\n",
    "\n",
    "FinalPredProba = VoteSyssb.predict_proba(X_test)\n",
    "print(confusion_matrix(y_test_sb,FinalPred))  \n",
    "print(classification_report(y_test_sb,FinalPred)) \n",
    "\n",
    "print(VoteSyssb.score(X_test,y_test_sb))  \n",
    "\n",
    "     \n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": []
  }
 ],
 "metadata": {
  "kernelspec": {
   "display_name": "Python 3",
   "language": "python",
   "name": "python3"
  },
  "language_info": {
   "codemirror_mode": {
    "name": "ipython",
    "version": 3
   },
   "file_extension": ".py",
   "mimetype": "text/x-python",
   "name": "python",
   "nbconvert_exporter": "python",
   "pygments_lexer": "ipython3",
   "version": "3.7.3"
  }
 },
 "nbformat": 4,
 "nbformat_minor": 2
}

        print("C= ", C_val)
        print("gamma= ", gamma_value)
        print(multilabel_confusion_matrix(y_test,predictions))  
        print(classification_report(y_test,predictions)) 
        print("Accuracy on training set: {:.3f}".format(svm.score(X_train, y_train)))
        print("Accuracy on test set: {:.3f}".format(svm.score(X_test2, y_test)))
        print("============================================")
    gamma_value = gamma_value + 0.05
    
print(predictions)
print(">>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>")
print("optimal C = ", optimal_C)
print("optimal gamma = ", optimal_gamma)


#compute the best SVC with optimal C value.
#svm_single=SVC(kernel="linear", gamma='auto_deprecated', C=optimal_C, probability=True) 
#svm=OneVsRestClassifier( SVC(kernel="linear", gamma='auto_deprecated', C=optimal_C, probability=True)  )
svm=OneVsRestClassifier( SVC(kernel="rbf", gamma=optimal_gamma, C=optimal_C)  )
svm.fit(X_train, y_train)
predictions = svm.predict(X_test2)
svm_pred=predictions


                                     
                                     

In [42]:
#Debugging purpose. Ignored
from sklearn.ensemble import VotingClassifier,BaggingClassifier
from sklearn.neural_network import MLPClassifier

'''
mlp=MLPClassifier(activation='logistic', alpha=0.9920073082747223,
              batch_size='auto', beta_1=0.9, beta_2=0.999, early_stopping=True,
              epsilon=1e-08)
mlp.fit(X_train, y_train)
print(mlp)

#print(dt.predict(X_test))

print(svm)

#print(svm.predict(X_test))
#Extracting ROW/COL/SB y and predict result from multilabel array as sklearn metrics may not support multilabel for bagging classifier.
y_train_row=[]
y_test_row=[]
dt_pred_row=[]
svm_pred_row=[]
mlp_pred_row=[]
for elem in y_train:
    y_train_row.append(elem[0])
for elem in y_test:    
    y_test_row.append(elem[0])
for elem in dt.predict(X_test):    
    dt_pred_row.append(elem[0])
for elem in svm.predict(X_test):    
    svm_pred_row.append(elem[0])
for elem in mlp.predict(X_test):    
    mlp_pred_row.append(elem[0])
    
y_train_col=[]
y_test_col=[]
dt_pred_col=[]
svm_pred_col=[]
mlp_pred_col=[]
for elem in y_train:
    y_train_col.append(elem[1])
for elem in y_test:    
    y_test_col.append(elem[1])
for elem in dt.predict(X_test):    
    dt_pred_col.append(elem[1])
for elem in svm.predict(X_test):    
    svm_pred_col.append(elem[1])
for elem in mlp.predict(X_test):    
    mlp_pred_col.append(elem[1])
    
y_train_sb=[]
y_test_sb=[]
dt_pred_sb=[]
svm_pred_sb=[]
mlp_pred_sb=[]
for elem in y_train:
    y_train_sb.append(elem[2])
for elem in y_test:    
    y_test_sb.append(elem[2])
for elem in dt.predict(X_test):    
    dt_pred_sb.append(elem[2])
for elem in svm.predict(X_test):    
    svm_pred_sb.append(elem[2])
for elem in mlp.predict(X_test):    
    mlp_pred_sb.append(elem[2])
        
#print(y_train_row)
false_pass_count=[
    confusion_matrix(y_test_row,dt_pred_row )[1][0] + confusion_matrix(y_test_col,dt_pred_col )[1][0] + confusion_matrix(y_test_sb,dt_pred_sb )[1][0],
    confusion_matrix(y_test_row,svm_pred_row )[1][0] + confusion_matrix(y_test_col,svm_pred_col )[1][0] + confusion_matrix(y_test_sb,svm_pred_sb )[1][0],
    confusion_matrix(y_test_row,mlp_pred_row ) [1][0] + confusion_matrix(y_test_col,mlp_pred_col )[1][0] + confusion_matrix(y_test_sb,mlp_pred_sb )[1][0]
]

#print(false_pass_count[0])
    

dt_row=dt.fit(X_train,y_train_row)
dt_col=dt.fit(X_train,y_train_col)
dt_sb=dt.fit(X_train,y_train_sb)


mlp_row=mlp.fit(X_train,y_train_row)
mlp_col=mlp.fit(X_train,y_train_col)
mlp_sb=mlp.fit(X_train,y_train_sb)

svm_row=svm_single.fit(X_train,y_train_row)
svm_col=svm_single.fit(X_train,y_train_col)
svm_sb=svm_single.fit(X_train,y_train_sb)


for i in range(3):
    if max(false_pass_count)==false_pass_count[i]:
        if i==1:
            dt2=eval("RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',\
            max_depth=%s, max_features='auto', max_leaf_nodes=None,\
            min_impurity_decrease=%s, min_impurity_split=None,\
            min_samples_leaf=1, min_samples_split=2,\
            min_weight_fraction_leaf=%s, n_estimators=50, n_jobs=None,\
            oob_score=False, random_state=0, verbose=0, warm_start=False)" % (best_depth,best_impurity_decrease,best_weight_fraction_leaf) )
            dt_row2=dt2.fit(X_train,y_train_row)
            dt_col2=dt2.fit(X_train,y_train_col)
            dt_sb2=dt2.fit(X_train,y_train_sb)
            dt_row=dt.fit(X_train,y_train_row)
            dt_col=dt.fit(X_train,y_train_col)
            dt_sb=dt.fit(X_train,y_train_sb)            
            
            if dt_row2.score(X_test,y_test_row)>dt_row.score(X_test,y_test_row):
                if dt_col2.score(X_test,y_test_col)>dt_col.score(X_test,y_test_col):
                    if dt_sb2.score(X_test,y_test_sb)>dt_sb.score(X_test,y_test_sb):
                        print("changed dt")
                        dt=dt2
                        dt.fit(X_train,y_train)
            dt_row=dt.fit(X_train,y_train_row)
            dt_col=dt.fit(X_train,y_train_col)
            dt_sb=dt.fit(X_train,y_train_sb)
        elif i==2:
            svm2=BaggingClassifier(base_estimator=svm, n_estimators=10)
            svm_row2=svm2.fit(X_train,y_train_row)
            svm_col2=svm2.fit(X_train,y_train_col)
            svm_sb2=svm2.fit(X_train,y_train_sb)
            svm_row=svm_single.fit(X_train,y_train_row)
            svm_col=svm_single.fit(X_train,y_train_col)
            svm_sb=svm_single.fit(X_train,y_train_sb)            
            if svm_row2.score(X_test,y_test_row)>svm_row.score(X_test,y_test_row):
                if svm_col2.score(X_test,y_test_col)>svm_col.score(X_test,y_test_col):
                    if svm_sb2.score(X_test,y_test_sb)>svm_sb.score(X_test,y_test_sb):
                        print("changed svm")
                        svm=svm2         
            svm_row=svm.fit(X_train,y_train_row)
            svm_col=svm.fit(X_train,y_train_col)
            svm_sb=svm.fit(X_train,y_train_sb)
                        
        elif i==3:
            mlp2=BaggingClassifier(base_estimator=mlp, n_estimators=10)
            mlp_row2=mlp2.fit(X_train,y_train_row)
            mlp_col2=mlp2.fit(X_train,y_train_col)
            mlp_sb2=mlp2.fit(X_train,y_train_sb)
            mlp_row=mlp.fit(X_train,y_train_row)
            mlp_col=mlp.fit(X_train,y_train_col)
            mlp_sb=mlp.fit(X_train,y_train_sb)
            if mlp_row2.score(X_test,y_test_row)>mlp_row.score(X_test,y_test):
                if mlp_col2.score(X_test,y_test_col)>mlp_col.score(X_test,y_test):
                    if mlp_sb2.score(X_test,y_test_sb)>mlp_sb.score(X_test,y_test):
                        print("changed mlp")
                        mlp=mlp2
                        #mlp.fit(X_train,y_train)            
            mlp_row=mlp.fit(X_train,y_train_row)
            mlp_col=mlp.fit(X_train,y_train_col)
            mlp_sb=mlp.fit(X_train,y_train_sb)
        break

print(dt)
print(svm)
print(mlp)

            


#print (mlp_row.predict(X_test))
#VoteSysRow=VotingClassifier(estimators=[('first', dt_row), ('second',svm_row ),('third',mlp_row) ], voting='soft')
VoteSysRow=VotingClassifier(estimators=[('first', dt_row), ('second',svm_row ),('third',mlp_row) ], voting='soft')



print("%s" % VoteSysRow)
#print(y_test_row)
VoteSysRow=VoteSysRow.fit(X_train, y_train_row)


FinalPred = VoteSysRow.predict(X_test)
  
          


FinalPredProba = VoteSysRow.predict_proba(X_test)
print(confusion_matrix(y_test_row,FinalPred))  
print(classification_report(y_test_row,FinalPred)) 

print(VoteSysRow.score(X_test,y_test_row))  


raise
'''
                           


'\nmlp=MLPClassifier(activation=\'logistic\', alpha=0.9920073082747223,\n              batch_size=\'auto\', beta_1=0.9, beta_2=0.999, early_stopping=True,\n              epsilon=1e-08)\nmlp.fit(X_train, y_train)\nprint(mlp)\n\n#print(dt.predict(X_test))\n\nprint(svm)\n\n#print(svm.predict(X_test))\n#Extracting ROW/COL/SB y and predict result from multilabel array as sklearn metrics may not support multilabel for bagging classifier.\ny_train_row=[]\ny_test_row=[]\ndt_pred_row=[]\nsvm_pred_row=[]\nmlp_pred_row=[]\nfor elem in y_train:\n    y_train_row.append(elem[0])\nfor elem in y_test:    \n    y_test_row.append(elem[0])\nfor elem in dt.predict(X_test):    \n    dt_pred_row.append(elem[0])\nfor elem in svm.predict(X_test):    \n    svm_pred_row.append(elem[0])\nfor elem in mlp.predict(X_test):    \n    mlp_pred_row.append(elem[0])\n    \ny_train_col=[]\ny_test_col=[]\ndt_pred_col=[]\nsvm_pred_col=[]\nmlp_pred_col=[]\nfor elem in y_train:\n    y_train_col.append(elem[1])\nfor elem in y_

In [43]:
#Section 3: MLP

In [44]:
from sklearn.model_selection import train_test_split, cross_val_score, RandomizedSearchCV
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import classification_report, multilabel_confusion_matrix
import eli5
from eli5.sklearn import PermutationImportance
from sklearn.multiclass import OneVsRestClassifier, _fit_binary
from itertools import cycle, product
from sklearn.manifold import TSNE
import seaborn as sns
from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
import hyperopt.pyll.stochastic
import time
#from sklearn.externals.joblib import Parallel, delayed
from sklearn.ensemble import VotingClassifier
from joblib import Parallel, delayed

#Section 3.0 data preprossing

# Reading the data
failure = pd.read_csv('TargetData.csv')

# Inspecting the data
pd.options.display.max_rows = 1000
print(failure.shape)
print(failure.head(3).transpose()) # 3093 data points with 1 ID, 58 features and 5 targets
print(failure.describe().transpose()) # 3 features do not have any variance: 'gallop 1','gallop 5','Row Shift 7'



ModuleNotFoundError: No module named 'seaborn'

In [ ]:
# Set up the data and label
#X consists of 58 features. Each feature represents 1 test in the long test flow.
X = failure.drop(['ID', 'gallop 1', 'gallop 5', 'Row Shift 7', 'SB','COL', 'Margin', 'Block', 'ROW'], axis=1)
#Y can be one of ROW,COL,SB. ROW means the failure is on a row of memory array.
#COL means the failure is on a column of the cell array
#SB is single bit failure inside the memory
#Forming 8 class from 3 columns, coded as 0 to 7
#['Overkill','SB','COL','SB+COL','ROW','ROW+SB','ROW+COL','SB+ROW+COL']
  #y = failure.SB+2*failure.COL+4*failure.ROW

#Converting y to reflect multilabels
  #mlb = MultiLabelBinarizer()
  #y_converted = mlb.fit_transform(failure[['SB','COL','ROW']])

target = ['multilabels', 'SB', 'ROW', 'COL']
y = [None] * len(target)

y[0] = failure[['SB', 'ROW', 'COL']].values
n_classes = y[0].shape[1]

for (i, j) in zip(range(1, len(target)), ['SB', 'ROW', 'COL']):
    y[i] = failure[j].values
    
    

In [ ]:
#Section 3.1 t-SNE model
# Runnig the t-SNE model
i = ['SB', 'ROW', 'COL'] 

for i in i:
    failure[i] = failure[i].replace({0: 'Negative', 1: 'Positive'})

# Create a t-SNE model with learning rate 50
embedding = TSNE(n_components=2,
                 perplexity=30,
                 learning_rate=200.0,
                 verbose=10,
                 random_state=42)

# Fit and transform the t-SNE model on the numeric dataset
tsne_features = pd.DataFrame(embedding.fit_transform(X))

tsne_features_failure = tsne_features.join([failure['SB'], failure['ROW'], failure['COL']])


In [ ]:
# Color the points according to types of failure
sns.set(rc={'figure.figsize': (25,25), 'legend.fontsize': 25, 'xtick.labelsize': 25, 'ytick.labelsize': 25, 
            'lines.markersize': 12.5, 'axes.labelsize': 0, 'axes.titlesize': 24})

fig, ax = plt.subplots(3,1)

j = ['SB', 'ROW', 'COL']
k = ['Reds', 'Purples', 'Greens']
l = ['darkred', 'violet', 'darkgreen']

for (i, j, k, l) in zip(range(n_classes), j, k, l):
    
    ax[i].set_title('t-SNE Plot of {}'.format(j))
    
    sns.kdeplot(data=tsne_features_failure[tsne_features_failure[j] == 'Positive'][0],
                data2=tsne_features_failure[tsne_features_failure[j] == 'Positive'][1],
                cmap=k,
                shade=True,
                bw=3,
                cbar=True, 
                ax=ax[i])
    
    sns.scatterplot(x=tsne_features_failure[0],
                    y=tsne_features_failure[1],
                    hue=tsne_features_failure[j],
                    style=tsne_features_failure[j],
                    palette=['aqua', l],
                    alpha=0.05,
                    ax=ax[i])
    

In [ ]:
# Section 3.2 Building MLP
# Train/test split
y_train = [None] * len(target)
y_test = [None] * len(target)

for i in range(len(target)):
    X_train, X_test, y_train[i], y_test[i] = train_test_split(X, y[i],
                                                              test_size=1/3,
                                                              random_state=42,
                                                              stratify=y[0])
    
# Set up space dictionary with specified hyperparameters
space = {'hidden_layer_sizes': hp.choice('hidden_layer_sizes', range(1,56)),
         'activation': hp.choice('activation', ['logistic','tanh','relu', 'identity']),
         'solver': hp.choice('solver', ['lbfgs','sgd','adam']),
         'alpha': hp.uniform('alpha', 0.0001, 1000),
         'learning_rate': hp.choice('learning_rate', ['constant', 'invscaling', 'adaptive']),
         'learning_rate_init': hp.uniform('learning_rate_init', 0.001, 0.99),
         'power_t': hp.uniform('power_t', 0.01, 0.99)}

wave = -1

target_clf = [None] * len(target)
target_clf_fitted = [None] * len(target)
target_y_pred_proba = [None] * len(target)
target_y_pred = [None] * len(target)

for i in range(len(target)):
    target_clf[i] = [None] * 12
    target_clf_fitted[i] = [None] * 12
    target_y_pred_proba[i] = [None] * 12
    target_y_pred[i] = [None] * 12

for (i, j) in zip(range(len(target)), ['multilabels', 'SB', 'ROW', 'COL']):
    
    wave = wave + 1
    
    # Set up objective function
    def objective(params):
        params = {'hidden_layer_sizes': params['hidden_layer_sizes'],
                  'activation': params['activation'],
                  'solver': params['solver'],
                  'alpha': params['alpha'],
                  'learning_rate': params['learning_rate'],
                  'learning_rate_init': params['learning_rate_init'],
                  'power_t': params['power_t']}
        
        hyperopt_clf = MLPClassifier(max_iter=4000,
                                     random_state=42,
                                     warm_start=True,
                                     early_stopping=True,
                                     **params)

        best_score = cross_val_score(estimator=hyperopt_clf,
                                     X=X_train,
                                     y=y_train[i],
                                     cv=3,
                                     n_jobs=4,
                                     pre_dispatch=10).mean()
    
        loss = 1 - best_score
        return {'best_score': best_score, 'loss': loss, 'status': STATUS_OK,'eval_time': time.time()}

    # Run the algorithm
    trials = Trials()
    best = fmin(fn=objective,
           space=space,
           max_evals=100,
           rstate=np.random.RandomState(42),
           algo=tpe.suggest,
           trials=trials)
    
    print('{}----------'.format(j))
    
    best_score = [None] * len(trials.trials)
    best_score[0] = trials.results[0].get('best_score')

    searched_params_df = pd.DataFrame(trials.trials[0].get('misc').get('vals').values())
    searched_params_df = searched_params_df.transpose()

    for i in list(range(1, len(trials.trials))):
        new_df = pd.DataFrame(trials.trials[i].get('misc').get('vals').values())
        searched_params_df = searched_params_df.append(new_df.transpose())
        best_score[i] = trials.results[i].get('best_score')

    searched_params_df = searched_params_df.rename(columns={0: 'activation', 1: 'alpha', 2: 'hidden_layer_sizes', 
                                                            3: 'learning_rate', 4: 'learning_rate_init', 
                                                            5: 'power_t', 6: 'solver'})
    
    blankIndex = [''] * len(searched_params_df)
    searched_params_df.index = blankIndex
    
    i = ['activation', 'learning_rate', 'solver']
    j = ['logistic', 'constant', 'lbfgs']
    k = ['tanh', 'invscaling', 'sgd']
    l = ['relu', 'adaptive', 'adam']
    m = ['identity']

    for (i, j, k, l) in zip(i, j, k, l):
         searched_params_df[i] = searched_params_df[i].replace({0: j, 1: k, 2: l, 3: m})

    searched_params_df['best_score'] = best_score

    searched_params_df_sorted = searched_params_df.sort_values(by='best_score', 
                                                               axis=0, 
                                                               ascending=False)
    
    searched_params_df_sorted = searched_params_df_sorted[searched_params_df_sorted.hidden_layer_sizes != 0]

    print(searched_params_df_sorted.head(5).transpose())
    print('__________')
    
    # Learn to predict each class against the other
        
    for i in range(5):
        target_clf[wave][i] = MLPClassifier(max_iter=4000,
                                            random_state=42,
                                            warm_start=True,
                                            early_stopping=True,
                                            activation=searched_params_df_sorted.values[i][0],
                                            alpha=searched_params_df_sorted.values[i][1],
                                            hidden_layer_sizes=int(searched_params_df_sorted.values[i][2]),
                                            learning_rate=searched_params_df_sorted.values[i][3],
                                            learning_rate_init=searched_params_df_sorted.values[i][4],
                                            power_t=searched_params_df_sorted.values[i][5],
                                            solver=searched_params_df_sorted.values[i][6])
    
    if wave == 0:
        for i in range(5):
            target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])
            target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)
            target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)
    else:
        # Create and fit the voting classifier
        target_clf[wave][5] = VotingClassifier(estimators=[('first', target_clf[wave][0]), 
                                                           ('second', target_clf[wave][1]), 
                                                           ('third', target_clf[wave][2]), 
                                                           ('forth', target_clf[wave][3]),
                                                           ('fifth', target_clf[wave][4])],
                                                voting='soft',
                                                n_jobs=4)
    
        for i in range(6):
            target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])
            target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)
            target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)

    # Create the parameter grid
    ##param_grid = {'hidden_layer_sizes': list(product(range(1,56), range(1,56)))}
    
    # Create a random search object
    ##ran_clf = RandomizedSearchCV(estimator = MLPClassifier(max_iter=4000,
                                                           ##random_state=42,
                                                           ##warm_start=True,
                                                           ##early_stopping=True,
                                                           ##activation=searched_params_df_sorted.values[0][0],
                                                           ##alpha=searched_params_df_sorted.values[0][1],
                                                           ##learning_rate=searched_params_df_sorted.values[0][3],
                                                           ##learning_rate_init=searched_params_df_sorted.values[0][4],
                                                           ##power_t=searched_params_df_sorted.values[0][5],
                                                           ##solver=searched_params_df_sorted.values[0][6]),
                                 ##param_distributions=param_grid,
                                 ##n_iter=465,
                                 ##n_jobs=4,
                                 ##pre_dispatch=100,
                                 ##cv=3,
                                 ##random_state=42)

    ##ran_clf_fitted = ran_clf.fit(X_train, y_train[wave])

    #Configuration of Layer 1 & 2
    ##mean_test_score = list(ran_clf_fitted.cv_results_.get('mean_test_score'))
    ##hidden_layers = list(ran_clf_fitted.cv_results_.get('param_hidden_layer_sizes'))

    ##best_hidden_layers_df = pd.DataFrame({'Hidden Layers': hidden_layers, 'Mean Test Score': mean_test_score})

    ##blankIndex = [''] * len(best_hidden_layers_df)
    ##best_hidden_layers_df.index = blankIndex

    # Print out the best configuration of hidden layers
    ##best_hidden_layers_df_sorted = best_hidden_layers_df.sort_values(by='Mean Test Score', 
                                                                     ##axis=0, 
                                                                     ##ascending=False)

    ##print(best_hidden_layers_df_sorted.head(5).transpose())
    ##print()

    ##for i in range(6, 11):
        ##target_clf[wave][i] = MLPClassifier(max_iter=4000,
                                            ##random_state=42,
                                            ##warm_start=True,
                                            ##early_stopping=True,
                                            ##activation=searched_params_df_sorted.values[0][0],
                                            ##alpha=searched_params_df_sorted.values[0][1],
                                            ##hidden_layer_sizes=best_hidden_layers_df_sorted['Hidden Layers'].values[i-6],
                                            ##learning_rate=searched_params_df_sorted.values[0][3],
                                            ##learning_rate_init=searched_params_df_sorted.values[0][4],
                                            ##power_t=searched_params_df_sorted.values[0][5],
                                            ##solver=searched_params_df_sorted.values[0][6])
    
    ##if wave == 0:
        ##for i in range(6, 11):
            ##target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])
            ##target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)
            ##target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)
    ##else:
        # Create and fit the voting classifier
        ##target_clf[wave][11] = VotingClassifier(estimators=[('first', target_clf[wave][6]), 
                                                            ##('second', target_clf[wave][7]), 
                                                            ##('third', target_clf[wave][8]), 
                                                            ##('forth', target_clf[wave][9]),
                                                            ##('fifth', target_clf[wave][10])],
                                                ##voting='soft',
                                                ##n_jobs=4)
    
        ##for i in range(6, 12):
            ##target_clf_fitted[wave][i] = target_clf[wave][i].fit(X_train, y_train[wave])
            ##target_y_pred_proba[wave][i] = target_clf[wave][i].predict_proba(X_test)
            ##target_y_pred[wave][i] = target_clf[wave][i].predict(X_test)
    
    #sns.set(rc={'figure.figsize': (20,20), 'legend.fontsize': 25, 'xtick.labelsize': 20, 'ytick.labelsize': 20, 
            #'lines.markersize': 10, 'axes.labelsize': 20, 'axes.titlesize': 20})

    #first_hidden_layer = [None] * len(hidden_layers)
    #second_hidden_layer = [None] * len(hidden_layers)

    #for i in range(len(hidden_layers)):
        #first_hidden_layer[i] = hidden_layers[i][0]
        #second_hidden_layer[i] = hidden_layers[i][1]

    #ax = sns.scatterplot(x=first_hidden_layer,
                         #y=second_hidden_layer)
    #ax.set_title('Scatterplot of the Combination of the Number of Neurons in the First & Second Hidden Layers')
 
    # Color the points according to types of failure
    sns.set(rc={'figure.figsize': (35,40), 'legend.fontsize': 25, 'xtick.labelsize': 20, 'ytick.labelsize': 20, 
                'lines.markersize': 10, 'axes.labelsize': 0, 'axes.titlesize': 20})

    fig, ax = plt.subplots(7,1)

    j = ['Activation Function for the Hidden Layer', 'L2 Penalty', 'Number of Neurons', 
         'Learning Rate Schedule for Weight Updates', 'Initial Learning Rate', 'Exponent for Inverse Scaling Learning Rate',
         'Solver for Weight Optimization']
    k = ['activation', 'alpha', 'hidden_layer_sizes', 'learning_rate', 'learning_rate_init', 'power_t', 'solver']
    
    for (i, j, k) in zip(range(7), j, k):
    
        ax[i].set_title('{}---Searched Parameters of the {}'.format(target[wave], j))
        sns.scatterplot(x=list(range(0, len(trials.trials))), 
                        y=searched_params_df[k].values, 
                        ax=ax[i])
        


In [ ]:
# Print classification report
wave = -1

for (i, j) in zip(range(len(target)), ['multilabels', 'SB', 'ROW', 'COL']):
    wave = wave + 1
    
    print(j)
    
    if wave == 0:
        i = [0, 1, 2, 3, 4]
        j = ['1stBest_1Layer', '2ndBest_1Layer', '3rdBest_1Layer', '4thBest_1Layer', '5thBest_1Layer']

        for (i, j) in zip(i, j):
            print('{}----------'.format(j))
            print()
            print(multilabel_confusion_matrix(y_true=y_test[wave], 
                                              y_pred=target_y_pred[wave][i]))
            print(classification_report(y_true=y_test[wave], 
                                        y_pred=target_y_pred[wave][i],
                                        target_names=['SB', 'ROW', 'COL'],
                                        digits=2))
    else:
        i = [0, 1, 2, 3, 4, 5]
        j = ['1stBest_1Layer', '2ndBest_1Layer', '3rdBest_1Layer', '4thBest_1Layer', '5thBest_1Layer', 'CombineBest_1Layer']

        for (i, j) in zip(i, j):
            print('{}----------'.format(j))
            print()
            print(confusion_matrix(y_true=y_test[wave], 
                                   y_pred=target_y_pred[wave][i]))
            print(classification_report(y_true=y_test[wave], 
                                        y_pred=target_y_pred[wave][i],
                                        target_names=['NonFault', 'Fault'],
                                        digits=2))
            

In [ ]:
# Computing feature importance
print('Best MLP estimator: {}'.format(target_clf[0][0]))
print()
print('Best results')
print(multilabel_confusion_matrix(y_true=y_test[0], 
                                  y_pred=target_y_pred[0][0]))
print(classification_report(y_true=y_test[0], 
                            y_pred=target_y_pred[0][0],
                            target_names=['SB', 'ROW', 'COL'],
                            digits=2))

perm = PermutationImportance(estimator=target_clf[0][0],
                             n_iter=100,
                             random_state=42).fit(X_test, y_test[0])

# Create a dataframe of the variables and feature importances
feature_importances_df = pd.DataFrame({'Variable': X.columns, 'Feature_Importances': perm.feature_importances_})

# Print out the top 3 positive variables
feature_importances_df_sorted = feature_importances_df.sort_values(by='Feature_Importances', 
                                                                   axis=0, 
                                                                   ascending=False)
print()
print(feature_importances_df_sorted)

mlp=target_clf[0][0]

In [ ]:
#Section 4: Re-train chance of individual based on competition result.

In [ ]:
from sklearn.ensemble import VotingClassifier

X_train,X_test,y_train,y_test=X_train_b,X_test_b,y_train_b,y_test_b

mlp1=eval("%s" % mlp)



#print(svm.predict(X_test))
#Extracting ROW/COL/SB y and predict result from multilabel array as sklearn metrics may not support multilabel for bagging classifier.
y_train_row=[]
y_test_row=[]
dt_pred_row=[]
svm_pred_row=[]
for elem in y_train:
    y_train_row.append(elem[0])
for elem in y_test:    
    y_test_row.append(elem[0])
for elem in dt.predict(X_test):    
    dt_pred_row.append(elem[0])
for elem in svm.predict(X_test):    
    svm_pred_row.append(elem[0])
#for elem in mlp1.predict(X_test):    
#    mlp_pred_row.append(elem[0])
    
y_train_col=[]
y_test_col=[]
dt_pred_col=[]
svm_pred_col=[]
for elem in y_train:
    y_train_col.append(elem[1])
for elem in y_test:    
    y_test_col.append(elem[1])
for elem in dt.predict(X_test):    
    dt_pred_col.append(elem[1])
for elem in svm.predict(X_test):    
    svm_pred_col.append(elem[1])
#for elem in mlp1.predict(X_test):    
#    mlp_pred_col.append(elem[1])
    
y_train_sb=[]
y_test_sb=[]
dt_pred_sb=[]
svm_pred_sb=[]
for elem in y_train:
    y_train_sb.append(elem[2])
for elem in y_test:    
    y_test_sb.append(elem[2])
for elem in dt.predict(X_test):    
    dt_pred_sb.append(elem[2])
for elem in svm.predict(X_test):    
    svm_pred_sb.append(elem[2])
#for elem in mlp1.predict(X_test):    
#    mlp_pred_sb.append(elem[2])

dt_row=dt.fit(X_train,y_train_row)
dt_col=dt.fit(X_train,y_train_col)
dt_sb=dt.fit(X_train,y_train_sb)


mlp_row=mlp1.fit(X_train,y_train_row)
mlp_col=mlp1.fit(X_train,y_train_col)
mlp_sb=mlp1.fit(X_train,y_train_sb)

mlp_pred_sb=mlp_sb.predict(X_test)
mlp_pred_row=mlp_row.predict(X_test)
mlp_pred_col=mlp_col.predict(X_test)

svm_row=svm_single.fit(X_train,y_train_row)
svm_col=svm_single.fit(X_train,y_train_col)
svm_sb=svm_single.fit(X_train,y_train_sb)



#print(y_train_row)
false_pass_count=[
    confusion_matrix(y_test_row,dt_pred_row )[1][0] + confusion_matrix(y_test_col,dt_pred_col )[1][0] + confusion_matrix(y_test_sb,dt_pred_sb )[1][0],
    confusion_matrix(y_test_row,svm_pred_row )[1][0] + confusion_matrix(y_test_col,svm_pred_col )[1][0] + confusion_matrix(y_test_sb,svm_pred_sb )[1][0],
    confusion_matrix(y_test_row,mlp_pred_row ) [1][0] + confusion_matrix(y_test_col,mlp_pred_col )[1][0] + confusion_matrix(y_test_sb,mlp_pred_sb )[1][0]
]

#print(false_pass_count[0])
    

for i in range(3):
    if max(false_pass_count)==false_pass_count[i]:
        if i==1:
            dt2=eval("RandomForestClassifier(bootstrap=True, class_weight=None, criterion='entropy',\
            max_depth=%s, max_features='auto', max_leaf_nodes=None,\
            min_impurity_decrease=%s, min_impurity_split=None,\
            min_samples_leaf=1, min_samples_split=2,\
            min_weight_fraction_leaf=%s, n_estimators=128, n_jobs=None,\
            oob_score=False, random_state=0, verbose=0, warm_start=False)" % (best_depth,best_impurity_decrease,best_weight_fraction_leaf) )
            dt_row2=dt2.fit(X_train,y_train_row)
            dt_col2=dt2.fit(X_train,y_train_col)
            dt_sb2=dt2.fit(X_train,y_train_sb)
            dt_row=dt.fit(X_train,y_train_row)
            dt_col=dt.fit(X_train,y_train_col)
            dt_sb=dt.fit(X_train,y_train_sb)            
            
            if dt_row2.score(X_test,y_test_row)>dt_row.score(X_test,y_test_row):
                if dt_col2.score(X_test,y_test_col)>dt_col.score(X_test,y_test_col):
                    if dt_sb2.score(X_test,y_test_sb)>dt_sb.score(X_test,y_test_sb):
                        print("changed dt")
                        dt=dt2
                        dt.fit(X_train,y_train)
            dt_row=dt.fit(X_train,y_train_row)
            dt_col=dt.fit(X_train,y_train_col)
            dt_sb=dt.fit(X_train,y_train_sb)
        elif i==2:
            svm2=BaggingClassifier(base_estimator=svm, n_estimators=10)
            svm_row2=svm2.fit(X_train,y_train_row)
            svm_col2=svm2.fit(X_train,y_train_col)
            svm_sb2=svm2.fit(X_train,y_train_sb)
            svm_row=svm_single.fit(X_train,y_train_row)
            svm_col=svm_single.fit(X_train,y_train_col)
            svm_sb=svm_single.fit(X_train,y_train_sb)            
            if svm_row2.score(X_test,y_test_row)>svm_row.score(X_test,y_test_row):
                if svm_col2.score(X_test,y_test_col)>svm_col.score(X_test,y_test_col):
                    if svm_sb2.score(X_test,y_test_sb)>svm_sb.score(X_test,y_test_sb):
                        print("changed svm")
                        svm=svm2         
            svm_row=svm.fit(X_train,y_train_row)
            svm_col=svm.fit(X_train,y_train_col)
            svm_sb=svm.fit(X_train,y_train_sb)
                        
        elif i==3:
            mlp2=BaggingClassifier(base_estimator=mlp, n_estimators=10)
            mlp_row2=mlp2.fit(X_train,y_train_row)
            mlp_col2=mlp2.fit(X_train,y_train_col)
            mlp_sb2=mlp2.fit(X_train,y_train_sb)
            mlp_row=mlp.fit(X_train,y_train_row)
            mlp_col=mlp.fit(X_train,y_train_col)
            mlp_sb=mlp.fit(X_train,y_train_sb)
            if mlp_row2.score(X_test,y_test_row)>mlp_row.score(X_test,y_test):
                if mlp_col2.score(X_test,y_test_col)>mlp_col.score(X_test,y_test):
                    if mlp_sb2.score(X_test,y_test_sb)>mlp_sb.score(X_test,y_test):
                        print("changed mlp")
                        mlp=mlp2
                        #mlp.fit(X_train,y_train)            
            mlp_row=mlp.fit(X_train,y_train_row)
            mlp_col=mlp.fit(X_train,y_train_col)
            mlp_sb=mlp.fit(X_train,y_train_sb)
        break

print(dt)
print(svm)
print(mlp)



In [ ]:
#Section 5: Voting ensemble as final output of the system

VoteSysRow=VotingClassifier(estimators=[('first', dt_row), 
                            ('second',svm_row ) ,                            
                            ('third',mlp_row ) 
                                       ],
                                                voting='soft')

#print(y_test_row)
VoteSysRow=VoteSysRow.fit(X_train, y_train_row)
print(VoteSysRow)

FinalPred = VoteSysRow.predict(X_test)
  
          


FinalPredProba = VoteSysRow.predict_proba(X_test)
print(confusion_matrix(y_test_row,FinalPred))  
print(classification_report(y_test_row,FinalPred)) 

print(VoteSysRow.score(X_test,y_test_row))  

                           
#X_train,X_test,y_train_col,y_test_col = train_test_split(X,test_data.COL,test_size=1/3,random_state=2, stratify=test_data.COL)


dt_col=dt.fit(X_train,y_train_col)
svm_col=svm_single.fit(X_train,y_train_col)
mlp_col=mlp1.fit(X_train,y_train_col)
#print (svm_col.predict(X_test))
VoteSyscol=VotingClassifier(estimators=[('first', dt_col), 
                            ('second',svm_col ) ,                            
                            ('third',mlp_col ) 
                                       ],
                                                voting='soft')

#print(y_test_col)
VoteSyscol=VoteSyscol.fit(X_train, y_train_col)
print(VoteSyscol)

FinalPred = VoteSyscol.predict(X_test)
  
          


FinalPredProba = VoteSyscol.predict_proba(X_test)
print(confusion_matrix(y_test_col,FinalPred))  
print(classification_report(y_test_col,FinalPred)) 

print(VoteSyscol.score(X_test,y_test_col))  

#X_train,X_test,y_train_sb,y_test_sb = train_test_split(X,test_data.SB,test_size=1/3,random_state=2, stratify=test_data.SB)


dt_sb=dt.fit(X_train,y_train_sb)
svm_sb=svm_single.fit(X_train,y_train_sb)
mlp_sb=mlp1.fit(X_train,y_train_sb)
#print (svm_sb.predict(X_test))
VoteSyssb=VotingClassifier(estimators=[('first', dt_sb), 
                            ('second',svm_sb ) ,                            
                            ('third',mlp_sb ) ,
                                       ],
                                                voting='soft')

#print(y_test_sb)
VoteSyssb=VoteSyssb.fit(X_train, y_train_sb)
print(VoteSyssb)

FinalPred = VoteSyssb.predict(X_test)
  
          


FinalPredProba = VoteSyssb.predict_proba(X_test)
print(confusion_matrix(y_test_sb,FinalPred))  
print(classification_report(y_test_sb,FinalPred)) 

print(VoteSyssb.score(X_test,y_test_sb))  

     
